# Working with accent data in the Mozilla Common Voice dataset 

The purpose of this Python Jupyter notebook is to provide some worked examples of how you might explore accent data in the Common Voice dataset. 



## Index of notebook contents 

To make this notebook easier to navigate, each section is indexed below. 

* [Background information on demographic data in Common Voice](#Background)
* [Preparation steps and importing modules](#PreparationSteps) - including the `requirements.txt` you should run if using this notebook. 
* [The Accent and AccentDescriptor classes we will use in the notebook](#Classes)
* [Preparing data from the Common Voice TSV file](#PreparingData)
* [Extracting accent information for data visualisation](#AccentExtraction)
* [Determine which accents are predetermined for selection in the Common Voice profile screen](#PreDetermined)
* [Add Descriptors to each Accent](#Descriptors)

---
<a id='Background'></a>
## Background information on demographic data in Common Voice 

Before you start working with accent data in Common Voice, there is background information you should know about the data structures in the Common Voice datasets, and how accents have been represented. 

### The ability to choose whether or not to specify demographic information 

Data contributors can contribute voice data to Common Voice with our without logging in to the platform. If a data contributor is not logged in, the utterances they record contain no demographic metadata information, such as the gender, age range or accent of the speaker. If the data contributor _does_ log in, then they can choose whether to specify demographic information in their profile. Part of the demographic information can include specifying which accent(s) they speak with. 


Since mid 2021, data contributors to the Common Voice dataset have been able to self-specify descriptors for their accents. 

The purpose of this script is to get demographic details from an MCV downloaded dataset. 
This informs decision making around, for example, how much of the data in a particular language, has demographic details, and if so, what they are. 

---
<a id='PreparationSteps'></a>

## Preparation steps and importing the modules we will use 

@TODO 

make a `requirements.txt` file to install all the dependencies. 

* pandas 


In [1]:
# imports go here 

# io 
import io

# os for file handling 
import os 

# pandas 
import pandas as pd

# regular expressions 
import re

# json 
import json

# string handling for isascii
import string 

# pretty print 
import pprint
pp = pprint.PrettyPrinter(indent=4)

# reload = because I'm developing the CVaccents module as I go, I want to reload it each time so it doesn't cache
from importlib import reload

# copy = for using deepcopy()
import copy

---
<a id='Classes'></a>
## Accent, AccentDescriptor and AccentCollection classes used for manipulation

In [2]:
## Accent class and AccentDescriptor class 

# these are classes I defined for accent handling
import cvaccents as cva

# do an explicit reload as I'm still working on the classes 
#reload(cva)

# prove that my DocStrings are useful
# they are good, so I am suppressing output while I work through the rest of the doc. 

#print('Module docstring is: \n', cva.__doc__)
#print('---')
#print('Accent docstring is: \n', cva.Accent.__doc__)
#print('---')
#print('AccentDescriptor docstring is: \n', cva.AccentDescriptor.__doc__)
#print('---')
#print('AccentCollection docstring is: \n', cva.AccentDescriptor.__doc__)
#print('---')

---
<a id='PreparingData'></a>
## Preparing the data from the Common Voice dataset TSV file

Here, we extract data from the TSV file, and use `pandas` to perform manipulations on the dataset, such as removing rows that do not contain accent metadata. 

In [3]:
# specify the path to the TSV file - this should be `validated.tsv` from the MCV download 
#filePath = '/media/kathyreid/Seagate Backup Plus Drive/cv-datasets/ru/validated.tsv'
#filePath = '/media/kathyreid/Seagate Backup Plus Drive/cv-datasets/fr/validated.tsv'
#filePath = '/media/kathyreid/Elements/de/validated.tsv'
#filePath = '/media/kathyreid/Elements/es/validated.tsv'
#filePath = '/media/kathyreid/Elements/en/validated.tsv'
#filePath = '/media/kathyreid/Seagate Backup Plus Drive/cv-datasets/en-v9/validated.tsv'
filePath = '../cv-datasets/cv-corpus-11.0-2022-09-21/en/validated.tsv'

# put it into a DataFrame 
df = pd.read_csv(filePath, sep='\t')

In [4]:
df.columns

Index(['client_id', 'path', 'sentence', 'up_votes', 'down_votes', 'age',
       'gender', 'accents', 'locale', 'segment'],
      dtype='object')

In [5]:
# We don't want all the columns, as some of them are not useful for the accent analysis 
# Drop the columns we don't want 

df.drop(labels=['path', 'sentence', 'up_votes', 'down_votes', 'segment', 'locale'], axis='columns', inplace=True)
df.columns



Index(['client_id', 'age', 'gender', 'accents'], dtype='object')

In [6]:
len(df)

1617877

In [7]:
# rows that have accent metadata 
len(df[df['accents'].notna()])

861134

In [8]:
# remove all the rows where accents are not given (NaN)
# https://pandas.pydata.org/pandas-docs/stable/reference/api/pandas.DataFrame.dropna.html
# DataFrame.dropna(*, axis=0, how=_NoDefault.no_default, thresh=_NoDefault.no_default, subset=None, inplace=False)

df.dropna(axis='index', how='any', subset='accents', inplace=True)
len(df)

# this matches the above figure for rows that have accent metadata, so it's a good cross-check

861134

In [9]:
# number of unique contributors to the dataset 
len(df['client_id'].unique())

14822

In [10]:
# Now that the rows without an accent value have been removed, 
# we want to deduplicate the speaker_id values - because one speaker can speak many utterances
# and we only want to record one accent per speaker 
# and we should end up with the # of rows in the cell above 


# One of the reasons we try and reduce the size of the dataframe 
# first is because this operation is more efficient on a smaller dataframe 
# https://pandas.pydata.org/docs/reference/api/pandas.DataFrame.drop_duplicates.html
# DataFrame.drop_duplicates(subset=None, *, keep='first', inplace=False, ignore_index=False)

df.drop_duplicates(subset='client_id', keep='first', inplace=True)
len(df)

# This length should match the length above 

14822

---
<a id='AccentExtraction'></a>
## Extracting the accent data for visualisation 

We have already: 

* Removed any rows where accent data was not available = `NaN`
* De-duplicated based on the `client_id`

So now, we need to extract all the self-styled accents for analysis. 

In [11]:
# They are already unique so we don't need the `.unique` method
english_accents = df['accents']

print(len(english_accents))

14822


In [12]:
"""

The list english_accents_list is a list that contains the ORIGINAL accent entries for each speaker. 
In this list, the accents for each speaker are represented as a SINGLE STRING, NOT as a list of strings. 

So, we want to turn this into a LIST of LISTS OF STRINGS, to make it easier for doing data cleaning. 
Each individual string represents one accent descriptor given by a speaker, 
and the list which contains those strings is the grouping of accent descriptors for that speaker. 

We need to preserve the association between accent descriptors - co-references - for later data visualisation. 

"""


english_accents_list = [] 

for idx, accent_string in list(enumerate(english_accents)): 
    
    # this regex is from 
    # https://stackoverflow.com/questions/26633452/how-to-split-by-commas-that-are-not-within-parentheses
    accent_list=re.split(',\s*(?![^()]*\))', accent_string)
    processed_accent_list = accent_list # we don't want to modify a list we're iterating over
    
    #print ('accent_string is: ', accent_string, ' and accent_list is: ', accent_list)
    for idx_a, accent in list(enumerate(accent_list)): 
        
        #print ('idx_a is: ', idx_a, ' and accent is: ', accent, ' and type of accent is: ', type(accent))
        # Trim any whitespace off the elements, because this makes matching on strings harder later on
        # Strings are immutable in Python, so we have to create another string
        processed_accent_list.remove(accent)
        stripped_accent = accent.strip() 
        processed_accent_list.append(stripped_accent)
        
        # Check for any empty strings and remove them - likely regex artefacts
        if not accent: 
            processed_accent_list.remove(accent)
            
        # Check for any non-Latin characters that we may want to investigate 
        # For example, if one of the accents is garbage or deliberate rubbish
        
        if not accent.isascii(): 
            print('flagging that accent: ', accent, ' is not ASCII encoded, may be in another language')
            
    english_accents_list.append(processed_accent_list)

flagging that accent:  Выраженный украинский акцент  is not ASCII encoded, may be in another language
flagging that accent:  Porto des dels 3 anys aprenent anglès a l'escola i actualment m'estic preparant per a l'examen del B2.  is not ASCII encoded, may be in another language


In [13]:
print(len(english_accents_list))

14822


In [14]:
for idx, accent_list in list(enumerate(english_accents_list)): 
    print(idx, accent_list)


0 ['England English', 'United States English']
1 ['Hong Kong English']
2 ['England English']
3 ['United States English']
4 ['United States English', 'wolof']
5 ['England English']
6 ['Australian English']
7 ['United States English']
8 ['Latin America', 'United States English']
9 ['United States English']
10 ['United States English']
11 ['Southern African (South Africa, Zimbabwe, Namibia)']
12 ['United States English']
13 ['United States English']
14 ['India and South Asia (India, Pakistan, Sri Lanka)']
15 ['United States English']
16 ['United States English']
17 ['England English']
18 ['India and South Asia (India, Pakistan, Sri Lanka)']
19 ['England English']
20 ['United States English']
21 ['Southern African (South Africa, Zimbabwe, Namibia)']
22 ['Australian English']
23 ['England English']
24 ['India and South Asia (India, Pakistan, Sri Lanka)']
25 ['United States English']
26 ['United States English', 'Colombia']
27 ['India and South Asia (India, Pakistan, Sri Lanka)']
28 ['India 

---
<a id='Descriptors'></a>
## Add descriptors to each accent

In this section, I apply a set of categories to the accent data. 

**I use a rule-based approach for reproduceability.** 
This could have been done in a spreadsheet, but I'm working in Python so I chose to do it that way. 
This also makes it easier for others applying this work to other languages or to other versions of the dataset. 



### Expand accents that have multiple descriptors in their .name element 

Here, we "break apart" accents that have multiple descriptors in the .name element into **multiple** accents. This is done _programmatically_ to aid in reproduceability. 

Some examples of this that I found during analysis were; 

* 8233 - 'south German / Swiss accent' - needs to be separated into 'South German' and 'Swiss accent'
* 6967 - 'slight Brooklyn Accent' - needs to be separated into "slight" and 'Brooklyn' - as a strength indicator 
* 10142 - 'minor French Accent' - needs to be separated into "minor" as an accent strength indicator, and 'French'
* 9902 - 'little Latino' - needs to be separated into "little" as an accent strength indicator, and "Latino"
* 3422 - 'i have some pronunciation issues because of oral surgery and a hidden southern accent' - needs to be separated into 'hidden southern accent' and 'changes due to Oral surgery'
* 9337 - 'heavy Cantonese' - needs to be separated into accent strength and country
* 1721 - 'United States English combined with European English' = needs to be separated into two accents
* 5365 - 'Sydney - middle eastern seaboard Australian' - should be separated into two accents
* 6615 - 'Spoke Chinese when little' - should be separated into Chinese, and speaking a different language as a child
* 748 - 'Spanish bilingual' - should be separated into 'Spanish' and 'bilingual ' as an Ln marker. 
* 6942 - 'South London and Essex' - should be separated into 'South London' and 'Essex'
* 12055 - 'Some time spent in Scotland' - should be separated into 'Scottish English' and into an Ln marker of "time spent in regional location"
* 773 - 'Silicon Valley Native' - should be separated into 'Silicon Valley' and "native" marker
* 3033 - "Porto des dels 3 anys aprenent anglès a l'escola i actualment m'estic preparant per a l'examen del B2." - this should be split into French, and academic register / L2 status
* 4322 - 'Polish. Have lived in nine states.' - should be separated into Polish and "lived in nine states" as a regional variance indicator or mixed accent indicator
* 5046 - 'Pittsburgh PA' - should be separated into Pittsburgh - city descriptor - and Pennsylvania as a regional descriptor. 
* 58 - 'Non native speaker from France' - should be separated into 'French' and 'Non native speaker'
* 1054 - 'Mild Northern England English' - should be separated into 'Northern England' and 'mild' for the strength of accent
* 11587 - 'Midwestern States (Michigan)' - should be separated into Midwestern and Michigan
* 1317 - 'Midwest USA speech blended with South Texas USA speech' - should be separated into Midwest and South Texas
* 1491 - 'Midwest US... With some Canadian slang. ' - should be separated into Midwest and Canadian Slang as register
* 'International Indian Accent' - should be separated into "Indian" and into "International"
* 2703 - 'Indian with a tinge of an RP accent' - should be separated into "Indian" and "Received Pronunciation" as well as an accent strength marker
* 1011 - 'I am German and speak English as learned at school' - should be separated into "German" and a register marker "as learned at school"
* 4839 - 'French mid level' - should be separated into 'French' and 'mid-level' as a fluency marker
* 1055 - 'England non-native' - should be separated into 'England' and 'Non-native' as a fluency marker
* 5305 - 'Educated Australian Accent' - should be separated into 'Australian' and 'Educated' as a register marker
* 12958 - 'CARIBBEAN AND BRITISH MIXED WITH SOME NEW YORK ACCENTS' - should be separated into three accents 
* 1577 - 'British English with a little bit of Russian' - should be separated into two accents. It's also an accent strength marker.
* 7271 - 'A variety of Texan English with some German influence that has undergone the cot-caught merger' - should be split into Texan, German influence, and a phonetic descriptor
* 6616 - '90% Pennsylvanian accent' - should be separated into Pennsylvanian and an accent strength marker
* 4319 - '4 years in Spain and Germany' - should be separated into French, German and a time or exposure marker
* 6617 - '10% Chinese accent' - should be separated into Chinese and an accent strength marker




### Modify the accent list to expand descriptors while preserving accent co-references

Some of the given accent descriptors contain multiple descriptors in one string. Here, I expand them while maintain co-references. 

For example: 

* `slight Brooklyn accent`  - contains both a City-based descriptor and an accent strength descriptor. 
* `United States English combined with European English` - contains both a national descriptor and a supranational descriptor. 



It's easier to do this before we create Accent and AccentDescriptor objects. 

In [15]:
# helper function for the below 

def update_list_coreference(list_to_be_updated, old_entry, new_entry):
    # the accent list is a list of lists so we need to iterate through each one to find the element to update. 
    
    for idx, accent_list in list(enumerate(list_to_be_updated)):
        
        #print(idx, '- old accent_list is: ', accent_list)
        new_accent_list = accent_list
        
        for accent in accent_list:  
            match = False
            #print ('accent is: ', accent, ' and old_entry is: ', old_entry)
            
            if accent == old_entry:
                match = True 
                #print('accent is: ', accent, ' and old_entry is: ', old_entry, 'and new_entry is: ', new_entry)
                #print('accent is: ', accent, ' which matches ', old_entry)
                new_accent_list.remove(old_entry)
                
                for entry in new_entry: # there may be more than one
                    new_accent_list.append(entry)
                    #print('appending new entry: ', entry)
                
            if match: 
                print ('processed ', old_entry, ' to be ', new_entry, ' and the old accent list is: ', accent_list, ' and the new accent list is: ', new_accent_list)

        # recreate the list from keys, this removes duplicates
        # for example, a duplicate may be created due to normalisation or merger of accents 
        new_accent_list = list(dict.fromkeys(new_accent_list))
        
        #print('new_accent_list is: ', new_accent_list)
        #print('---')
        
        #print('removing: ', accent_list)
        list_to_be_updated.remove(accent_list)
        #print('appending: ', newlist)
        list_to_be_updated.append(new_accent_list)
        
    
    return(list_to_be_updated)

In [16]:
#'south German / Swiss accent' - needs to be separated into 'South German' and 'Swiss'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'south German / Swiss accent', 
                                               ['South German', 'Swiss'])

#'English with Swiss german accent - needs to be separated into 'Swiss German'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'English with Swiss german accent', 
                                               ['Swiss German'])

# 'slight Brooklyn Accent' - needs to be separated into "slight" and 'Brooklyn' - as a strength indicator  
english_accents_list = update_list_coreference(english_accents_list, 
                                               'slight Brooklyn Accent', 
                                               ['Brooklyn Accent', 'slight'])

# 'minor French Accent' - needs to be separated into "minor" as an accent strength indicator, and 'French'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'minor French Accent', 
                                               ['French', 'minor'])

# 'minor French Accent' - needs to be separated into "minor" as an accent strength indicator, and 'French'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'minor french accent', 
                                               ['French', 'minor'])

# French mid level accent - needs to be separated into "mid level" as an accent strength indicator, and 'French'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'French mid level accent', 
                                               ['French', 'mid level'])

# 'little Latino' - needs to be separated into "Latino" as an accent and 'little' as an accent strength indicator
english_accents_list = update_list_coreference(english_accents_list, 
                                               'little Latino', 
                                               ['Latino', 'little'])

# 'little Latino' - needs to be separated into "Latino" as an accent and 'little' as an accent strength indicator
english_accents_list = update_list_coreference(english_accents_list, 
                                               'little latino', 
                                               ['Latino', 'little'])

# 'heavy Cantonese' - needs to be separated into accent strength and country   
english_accents_list = update_list_coreference(english_accents_list, 
                                               'heavy Cantonese', 
                                               ['Cantonese', 'heavy'])

# 'United States English combined with European English' - needs to be separated into two accents
english_accents_list = update_list_coreference(english_accents_list, 
                                               'United States English combined with European English', 
                                               ['United States English', 'European English'])

# 'United States English Pacific Northwest' - needs to be separated into two accents
english_accents_list = update_list_coreference(english_accents_list, 
                                               'United States English Pacific Northwest', 
                                               ['United States English', 'Pacific Northwest'])
                                               
# 'Sydney - middle eastern seaboard Australian' - should be separated into two accent
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Sydney - middle eastern seaboard Australian', 
                                               ['Sydney', 'Middle eastern seaboard Australian'])
        
# 'Spoke Chinese when little' - should be separated into Chinese, and speaking a different language as a child
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Spoke Chinese when little', 
                                               ['Chinese', 'Spoke language when a child'])        
    
# 'Spanish bilingual' - should be separated into 'Spanish' and 'bilingual ' as an Ln marker. 
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Spanish bilingual', 
                                               ['Spanish', 'Bilingual']) 

# 'South London and Essex' - should be separated into 'South London' and 'Essex'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'South London and Essex' , 
                                               ['South London', 'Essex']) 

# 'Some time spent in Scotland' - should be separated into 'Scottish English' and into an Ln marker of "time spent in regional location"
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Some time spent in Scotland' , 
                                               ['Scottish English', 'some time spent in location']) 

# 'Silicon Valley Native' - should be separated into 'Silicon Valley' and "native" marker
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Silicon Valley Native' , 
                                               ['Silicon Valley', 'native']) 

# "Porto des dels 3 anys aprenent anglès a l'escola i actualment m'estic preparant per a l'examen del B2." - this should be split into French, and academic register / L2 status
english_accents_list = update_list_coreference(english_accents_list, 
                                               "Porto des dels 3 anys aprenent anglès a l'escola i actualment m'estic preparant per a l'examen del B2." , 
                                               ['French', 'academic', 'second language']) 


# Выраженный украинский акцент - this should be separated into 'Ukrainian' and 'pronounced'
# it literally means 'pronounced Ukrainian accent'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Выраженный украинский акцент' , 
                                               ['Ukrainian', 'pronounced']) 


# 'Polish. Have lived in nine states.' - should be separated into Polish and "lived in nine states" as a regional variance indicator or mixed accent indicator
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Polish. Have lived in nine states.',
                                               ['Polish', 'mixed']) 

# 'Pittsburgh PA' - should be separated into Pittsburgh - city descriptor - and Pennsylvania as a regional descriptor.
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Pittsburgh PA',
                                               ['Pittsburgh', 'Pennsylvania']) 

# 'Non native speaker from France' - should be separated into 'French' and 'Non native speaker'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Non native speaker from France',
                                               ['French', 'Non native']) 

# 'Mild Northern England English' - should be separated into 'Northern England' and 'mild' for the strength of accent
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Mild Northern England English',
                                               ['Northern English', 'Mild']) 

# 'Midwestern States (Michigan)' - should be separated into Midwestern and Michigan
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Midwestern States (Michigan)',
                                               ['Midwestern United States', 'Michigan']) 

# Midwest US... With some Canadian slang - should separated into Midwestern United States, Canadian English and 'slang' as a register
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Midwest US... With some Canadian slang.',
                                               ['Midwestern United States', 'Canadian English', 'slang']) 

# 'Midwest USA speech blended with South Texas USA speech' - should be separated into Midwest and South Texas
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Midwest USA speech blended with South Texas USA speech',
                                               ['Midwestern United States', 'South Texas']) 

# 'slighty Southern affected by decades in the Midwest' - should be separated into Southern United States, Midwestern United States and time spent in location
english_accents_list = update_list_coreference(english_accents_list, 
                                               'slighty Southern affected by decades in the Midwest',
                                               ['Midwestern United States', 'Southern United States', 'time spent in location']) 


# 'United States English. people say I sound like a surffer dude.' - should be separated into 'United States English' and 'surfer' as a register
english_accents_list = update_list_coreference(english_accents_list, 
                                               'United States English. people say I sound like a surffer dude.',
                                               ['United States English', 'surfer']) 


# 'new england/east coast' - should be separated into New England and East coast 
english_accents_list = update_list_coreference(english_accents_list, 
                                               'new england/east coast',
                                               ['New England', 'East coast']) 

# 'little bit classy little bit sassy and add some city.....thats me' - should be separated into 'United States English' and 'surfer' as a register
english_accents_list = update_list_coreference(english_accents_list, 
                                               'little bit classy little bit sassy and add some city.....thats me',
                                               ['little bit', 'classy', 'sassy', 'city']) 

# 'International Indian Accent' - should be separated into "Indian" and into "International"
english_accents_list = update_list_coreference(english_accents_list, 
                                               'International Indian Accent',
                                               ['India and South Asia (India, Pakistan, Sri Lanka)', 'International']) 


# 'Indian with a tinge of an RP accent' - should be separated into "Indian" and "Received Pronunciation" as well as an accent strength marker
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Indian with a tinge of an RP accent',
                                               ['India and South Asia (India, Pakistan, Sri Lanka)', 'Received Pronunciation', 'tinge']) 

# 'I am German and speak English as learned at school' - should be separated into "German" and a register marker "as learned at school"
english_accents_list = update_list_coreference(english_accents_list, 
                                               'I am German and speak English as learned at school',
                                               ['German', 'academic', 'second language']) 

# 'speak some German' - should be separated into 'German' and an accent 
english_accents_list = update_list_coreference(english_accents_list, 
                                               'speak some German',
                                               ['German', 'some'])

# 'French mid level' - should be separated into 'French' and 'mid-level' as a fluency marker
english_accents_list = update_list_coreference(english_accents_list, 
                                               'French mid level',
                                               ['French', 'Mid-level']) 


# 'England non-native' - should be separated into 'England' and 'Non-native' as a fluency marker
english_accents_list = update_list_coreference(english_accents_list, 
                                               'England non-native',
                                               ['England English', 'Non native'])


# 'Educated Australian Accent' - should be separated into 'Australian' and 'Educated' as a register marker
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Educated Australian Accent',
                                               ['Australian English', 'Educated'])

# 'CARIBBEAN AND BRITISH MIXED WITH SOME NEW YORK ACCENTS' - should be separated into three accents 
english_accents_list = update_list_coreference(english_accents_list, 
                                               'CARIBBEAN AND BRITISH MIXED WITH SOME NEW YORK ACCENTS',
                                               ['West Indies and Bermuda (Bahamas, Bermuda, Jamaica, Trinidad)', 'England English', 'New York'])

# 'British English with a little bit of Russian' - should be separated into two accents. 
# It's also an accent strength marker.
english_accents_list = update_list_coreference(english_accents_list, 
                                               'British English with a little bit of Russian',
                                               ['Russian', 'England English', 'little bit'])

# 'A variety of Texan English with some German influence that has undergone the cot-caught merger' 
#- should be split into Texan, German influence, and a phonetic descriptor
english_accents_list = update_list_coreference(english_accents_list, 
        'A variety of Texan English with some German influence that has undergone the cot-caught merger',
        ['Texas', 'German', 'some', 'cot-caught merger'])

# '90% Pennsylvanian accent' - should be separated into Pennsylvanian and an accent strength marker
english_accents_list = update_list_coreference(english_accents_list, 
                                               '90% Pennsylvanian accent',
                                               ['Pennsylvania', '90%'])

# '4 years in Spain and Germany' - should be separated into French, German and a time or exposure marker
english_accents_list = update_list_coreference(english_accents_list, 
                                               '4 years in Spain and Germany',
                                               ['Spanish', 'German', 'some time spent in location'])

# '10% Chinese accent' - should be separated into Chinese and an accent strength marker
english_accents_list = update_list_coreference(english_accents_list, 
                                               '10% Chinese accent',
                                               ['Chinese', '10%'])

# 'With heavy Cantonese accent' - should be separated into Cantonese and 'heavy' as an accent strength marker
english_accents_list = update_list_coreference(english_accents_list, 
                                               'With heavy Cantonese accent',
                                               ['heavy', 'Cantonese'])

# 'i have some pronunciation issues because of oral surgery and a hidden southern accent' - needs to be separated into 'hidden southern accent' and 'changes due to Oral surgery'
english_accents_list = update_list_coreference(english_accents_list, 
                'i have some pronunciation issues because of oral surgery and a hidden southern accent',
                ['Southern United States', 'changes due to oral surgery'])


# 'Indo-Canadian English' - needs to be separated into the canonical forms for Indian and Canadian
english_accents_list = update_list_coreference(english_accents_list, 
                'Indo-Canadian English',
                ['Canadian English', 'India and South Asia (India, Pakistan, Sri Lanka)'])


# Hmong-American - needs to be separated into United States and Hmong 
english_accents_list = update_list_coreference(english_accents_list, 
                'Hmong-American',
                ['United States English', 'Hmong'])



processed  south German / Swiss accent  to be  ['South German', 'Swiss']  and the old accent list is:  ['England English', 'South German', 'Swiss']  and the new accent list is:  ['England English', 'South German', 'Swiss']
processed  English with Swiss german accent  to be  ['Swiss German']  and the old accent list is:  ['Swiss German']  and the new accent list is:  ['Swiss German']
processed  slight Brooklyn Accent  to be  ['Brooklyn Accent', 'slight']  and the old accent list is:  ['United States English', 'Canadian English', 'Brooklyn Accent', 'slight']  and the new accent list is:  ['United States English', 'Canadian English', 'Brooklyn Accent', 'slight']
processed  minor french accent  to be  ['French', 'minor']  and the old accent list is:  ['French', 'minor']  and the new accent list is:  ['French', 'minor']
processed  French mid level accent  to be  ['French', 'mid level']  and the old accent list is:  ['french accent', 'French', 'mid level']  and the new accent list is:  ['fre

processed  speak some German  to be  ['German', 'some']  and the old accent list is:  ['4 years in Spain and Germany', 'Spanish', 'Polish', 'mixed', 'Midwestern United States', 'Southern United States', 'time spent in location', 'German', 'some']  and the new accent list is:  ['4 years in Spain and Germany', 'Spanish', 'Polish', 'mixed', 'Midwestern United States', 'Southern United States', 'time spent in location', 'German', 'some']
processed  England non-native  to be  ['England English', 'Non native']  and the old accent list is:  ['England English', 'Non native']  and the new accent list is:  ['England English', 'Non native']
processed  Educated Australian Accent  to be  ['Australian English', 'Educated']  and the old accent list is:  ['Australian English', 'Australian English', 'Educated']  and the new accent list is:  ['Australian English', 'Australian English', 'Educated']
processed  CARIBBEAN AND BRITISH MIXED WITH SOME NEW YORK ACCENTS  to be  ['West Indies and Bermuda (Bahama

### Normalize closely related accent descriptors - merge them 

There are several closely related accent descriptors, and here I merge them. 

The principles I use are: 
    
* Accents are merged where there are spelling variations 
* Accents are merged where the accent has a region descriptor with our without 'accent' - such as "French" and "French accent"
* Where a country or language descriptor and demonym are closely equivalent - "Germany" and "German"

Accents are not merged where: 

* One accent descriptor is more granular than another - "London" and "South London" are not merged. 

In [17]:
# I can just use the same function

## There will be others as we put them into objects / classes


# Midwestern - canonical is 'Midwestern United States'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Midwestern',
                                               ['Midwestern United States'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Midwestern United States English',
                                               ['Midwestern United States'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'midwestern US',
                                               ['Midwestern United States'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'midwest',
                                               ['Midwestern United States'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Unite States Midwest',
                                               ['Midwestern United States'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Midwestern US English (United States)',
                                               ['Midwestern United States'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Midwestern US English (United States)',
                                               ['Midwest United States'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Mid-west United States English',
                                               ['Midwest United States'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'American Midwest',
                                               ['Midwest United States'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Midwestern United States',
                                               ['Midwest United States'])



# Southern United States - canonical is 'Southern United States'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'southern United States',
                                               ['Southern United States'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Southern American English',
                                               ['Southern United States'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'southern',
                                               ['Southern United States'])


# Mid-atlantic - canonical is 'Mid-atlantic United States'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Mid-atlantic',
                                               ['Mid-atlantic United States'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Mid-Atlantic United States English',
                                               ['Mid-atlantic United States'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Midatlantic',
                                               ['Mid-atlantic United States'])


# Philadelphia - canonical is 'Philadelphia'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Philadelphia Style United States English',
                                               ['Philadelphia'])



# California - canonical is 'California'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Californian Accent',
                                               ['California'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Cali',
                                               ['California'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Californian',
                                               ['California'])

# Northern California - as distinct from California - canonical is 'Northern California'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'northern cali',
                                               ['Northern California'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Northern Californian',
                                               ['Northern California'])

# Southern California - as distinct from California - canonical is 'Southern California'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Southern Californian',
                                               ['Southern California'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Southern Cali',
                                               ['Southern California'])


# British - canonical is 'British'



# England - canonical is 'England English'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'england',
                                               ['England English'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'England',
                                               ['England English'])

# Scottish - canonical is 'Scottish English'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Scottish',
                                               ['Scottish English'])

# Northern England - canonical is 'Northern England'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Northern English',
                                               ['Northern England'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'English north of England',
                                               ['Northern England'])

# Durham - as distinct from Northern England - canonical is 'Durham'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'English County Durham',
                                               ['Durham'])

# Yorkshire - as distinct from Northern England - canonical is 'Yorkshire'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'yorkshire',
                                               ['Yorkshire'])

# Southern England - canonical is 'Southern England'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'southern english',
                                               ['Southern England'])


# Sussex - as distinct from Southern England - canonical is 'Sussex'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'sussex',
                                               ['Sussex'])

# London - canonical is 'London'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'London English',
                                               ['London'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'london',
                                               ['London'])


# Liverpool - canonical is 'Liverpool'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Liverpool English',
                                               ['Liverpool'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Liverpudlian English',
                                               ['Liverpool'])

# Lancashire - canonical is 'Lancashire'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Lancashire English',
                                               ['Lancashire'])

# Dutch - canonical is 'Dutch'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Dutch English',
                                               ['Dutch'])

# Swedish - canonical is 'Swedish'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'swedish',
                                               ['Swedish'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'swedish english',
                                               ['Swedish'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'swedish',
                                               ['Swedish'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Swedish English',
                                               ['Swedish'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Swedish accent',
                                               ['Swedish'])


# German - canonical is 'German'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'German Accent',
                                               ['German'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'German English',
                                               ['German'])

# South German - as distinct from German - canonical is 'South German'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'South German accent',
                                               ['South German'])

# South West German - as distinct from German 
english_accents_list = update_list_coreference(english_accents_list, 
                                               'south-west German',
                                               ['South West German'])

# French - canonical is 'French'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'french accent',
                                               ['French'])

# European - as distinct from Eastern European - canonical is 'European
english_accents_list = update_list_coreference(english_accents_list, 
                                               'European English',
                                               ['European'])

# Eastern Europe - canonical is 'Eastern European'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'eastern european English',
                                               ['Eastern European'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'eastern Europe',
                                               ['Eastern European'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'eastern europe',
                                               ['Eastern European'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'East European',
                                               ['Eastern European'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Eastern European English',
                                               ['Eastern European'])


# Polish - canonical is 'Polish'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Polish English',
                                               ['Polish'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'polish',
                                               ['Polish'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'polish accent',
                                               ['Polish'])


# 'serbian' - canonical is 'Serbian'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'serbian',
                                               ['Serbian'])

# Israeli - canonical is 'Israeli' 
english_accents_list = update_list_coreference(english_accents_list, 
                                               "Israeli's accent",
                                               ['Israeli'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Israeli accent',
                                               ['Israeli'])

# Nigerian - canonical is 'Nigerian'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Nigerian English',
                                               ['Nigerian'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'nigeria english',
                                               ['Nigerian'])

# Kenyan - canonical is 'Kenyan'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Kenyan English',
                                               ['Kenyan'])
# Wolof - canonical is 'Wolof'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'wolof',
                                               ['Wolof'])

# 'South African English' - canonical is 'Southern African (South Africa, Zimbabwe, Namibia)'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'South African English',
                                               ['Southern African (South Africa, Zimbabwe, Namibia)'])


# Latin American - canonical is 'Latino'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Latin American',
                                               ['Latino'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Latin American accent',
                                               ['Latino'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Latin America',
                                               ['Latino'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Hispanic/Latino',
                                               ['Latino'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Latin English',
                                               ['Latino'])

# Colombian - canonical is 'Colombian'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Colombian Accent',
                                               ['Colombian'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Colombia',
                                               ['Colombian'])



# Japanese - canonical is 'Japanese'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Japanese English',
                                               ['Japanese'])


#Bangladeshi - canonical is 'Bangladeshi'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Bangladesh',
                                               ['Bangladeshi'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'bangladesh',
                                               ['Bangladeshi'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Bangladesh English',
                                               ['Bangladeshi'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Bangladeshi English',
                                               ['Bangladeshi'])



# Non-native speaker descriptions - canonical is 'Non-native speaker'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Non-native',
                                               ['Non-native speaker'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Non native speaker',
                                               ['Non-native speaker'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Non native',
                                               ['Non-native speaker'])


# Second language descriptions - canonical is 'Second language'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'ESL',
                                               ['Second language'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'second language',
                                               ['Second language'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               '2nd Language',
                                               ['Second language'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'English as a Second Language',
                                               ['Second language'])

# International accent descriptions - canonical is 'International English'

english_accents_list = update_list_coreference(english_accents_list, 
                                               'International',
                                               ['International English'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'international',
                                               ['International English'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Transnational englishes blend',
                                               ['International English'])

# Mix of accents - canonical is 'Mix of accents'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Mix of voices',
                                               ['Mix of accents'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Mixed-Accent English',
                                               ['Mix of accents'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'mixed',
                                               ['Mix of accents'])


# Time spent in location - canonical is 'time spent in location'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'some time spent in location',
                                               ['time spent in location'])


# Little and little bit - canonical is 'little'

english_accents_list = update_list_coreference(english_accents_list, 
                                               'little bit',
                                               ['little'])


processed  Midwestern  to be  ['Midwestern United States']  and the old accent list is:  ['United States English', 'Midwestern United States']  and the new accent list is:  ['United States English', 'Midwestern United States']
processed  Midwestern  to be  ['Midwestern United States']  and the old accent list is:  ['United States English', 'Midwestern United States']  and the new accent list is:  ['United States English', 'Midwestern United States']
processed  Midwestern  to be  ['Midwestern United States']  and the old accent list is:  ['United States English', 'Minnesotan', 'Midwestern United States']  and the new accent list is:  ['United States English', 'Minnesotan', 'Midwestern United States']
processed  Midwestern  to be  ['Midwestern United States']  and the old accent list is:  ['United States English', 'Low', 'Demure', 'Midwestern United States']  and the new accent list is:  ['United States English', 'Low', 'Demure', 'Midwestern United States']
processed  Midwestern United S

processed  northern cali  to be  ['Northern California']  and the old accent list is:  ['Northern California']  and the new accent list is:  ['Northern California']
processed  Southern Californian  to be  ['Southern California']  and the old accent list is:  ['United States English', 'Southern California']  and the new accent list is:  ['United States English', 'Southern California']
processed  england  to be  ['England English']  and the old accent list is:  ['london', 'academic', 'England English']  and the new accent list is:  ['london', 'academic', 'England English']
processed  England  to be  ['England English']  and the old accent list is:  ['England English', 'Lancashire', 'England English']  and the new accent list is:  ['England English', 'Lancashire', 'England English']
processed  Scottish  to be  ['Scottish English']  and the old accent list is:  ['Scottish English', 'Scottish English']  and the new accent list is:  ['Scottish English', 'Scottish English']
processed  Norther

processed  polish accent  to be  ['Polish']  and the old accent list is:  ['Polish']  and the new accent list is:  ['Polish']
processed  serbian  to be  ['Serbian']  and the old accent list is:  ['United States English', 'Serbian']  and the new accent list is:  ['United States English', 'Serbian']
processed  Israeli's accent  to be  ['Israeli']  and the old accent list is:  ['Israeli']  and the new accent list is:  ['Israeli']
processed  Israeli accent  to be  ['Israeli']  and the old accent list is:  ['United States English', 'Israeli']  and the new accent list is:  ['United States English', 'Israeli']
processed  Nigerian English  to be  ['Nigerian']  and the old accent list is:  ['Nigerian']  and the new accent list is:  ['Nigerian']
processed  nigeria english  to be  ['Nigerian']  and the old accent list is:  ['Nigerian']  and the new accent list is:  ['Nigerian']
processed  Kenyan English  to be  ['Kenyan']  and the old accent list is:  ['United States English', 'Kenyan']  and the 

## Extract unique accents from the list of normalised accents into a Dict of Accent objects for easier manipulation

In [18]:
# build a dict of each unique accent using an Accent object for each object. 

ratio_display = 120 # to stop the browser crashing 

AccentDict = {}
i = 0; 

# the english_accents_list is now normalised, merged etc so this is straightforward 
for accent_list in english_accents_list:
    for accent in accent_list: 
        
        i +=1
        match = False 
        count = 0
        
        #if (i%ratio_display ==0): # only show the 100th 
            #print('')
            #print('---')
            #print('now processing: ', accent, ' - ', i)
            #print('---')
        
        # is this accent in our dict - if not, add it in 
        
        for item in AccentDict.items() : # Each item should be an Accent object 
            
            # (self, id=0, name="Accent Name", count=0, locale=None, descriptors=None):
            #pp.pprint(item[1].__str__())
            
            #if (i%ratio_display ==0): # only show the 100th 
                #print('item is: ', item)
                #print(type(item))
                #print('now checking match for: item:', item[1], ' and accent: ', accent)
            
            if (item[1].name == accent) : # update the count
                
                #if (i%ratio_display ==0): # only show the 100th 
                    #print('---')
                    #print('match is True')
                    #print('---')
                    
                match = True 
                
                #if (i%ratio_display ==0): # only show the 100th 
                    #print('accent count was: ', item[1].count)
                
                # update the count of the accent 
                item[1].count+=1
                
                #if (i%ratio_display ==0): # only show the 100th 
                    #print('accent count is now: ', item[1].count)
                
                
        # this match loop has to be outside the for: loop above 
        # because if we add items to the dict inside the loop
        # then it will not run - because there are zero items in the dict to begin with 
        
        if (not match) :   
            
            # (self, id=0, name="Accent Name", count=0, locale=None, descriptors=None):
            AccentDict[i] = cva.Accent(i, accent, 1, 'en', None, False) 
                


In [19]:
# do an explicit reload as I'm still working on the classes 
#reload(cva)

all_accents = cva.AccentCollection(AccentDict)

In [20]:
print(all_accents.total())

165


In [21]:
all_accents.__str__()

'id is 1, name is England English, count is 2346, locale is en, descriptors are None, predetermined is False. id is 2, name is United States English, count is 7537, locale is en, descriptors are None, predetermined is False. id is 3, name is Hong Kong English, count is 132, locale is en, descriptors are None, predetermined is False. id is 7, name is Wolof, count is 1, locale is en, descriptors are None, predetermined is False. id is 9, name is Australian English, count is 665, locale is en, descriptors are None, predetermined is False. id is 12, name is Latino, count is 7, locale is en, descriptors are None, predetermined is False. id is 15, name is Southern African (South Africa, Zimbabwe, Namibia), count is 261, locale is en, descriptors are None, predetermined is False. id is 18, name is India and South Asia (India, Pakistan, Sri Lanka), count is 2010, locale is en, descriptors are None, predetermined is False. id is 31, name is Colombian, count is 2, locale is en, descriptors are N

In [22]:
# do an explicit reload as I'm still working on the classes 
#reload(cva)

all_accents_sortedByCount = all_accents.sortByCount(reverse=True)

for accent in all_accents_sortedByCount.items(): 
    print(accent[1].__str__())
    
# now I am cross-checking to see if there are any other duplicates or accents that should be merged


id is 2, name is United States English, count is 7537, locale is en, descriptors are None, predetermined is False.
id is 1, name is England English, count is 2346, locale is en, descriptors are None, predetermined is False.
id is 18, name is India and South Asia (India, Pakistan, Sri Lanka), count is 2010, locale is en, descriptors are None, predetermined is False.
id is 37, name is Canadian English, count is 897, locale is en, descriptors are None, predetermined is False.
id is 9, name is Australian English, count is 665, locale is en, descriptors are None, predetermined is False.
id is 15, name is Southern African (South Africa, Zimbabwe, Namibia), count is 261, locale is en, descriptors are None, predetermined is False.
id is 302, name is Irish English, count is 188, locale is en, descriptors are None, predetermined is False.
id is 70, name is Scottish English, count is 172, locale is en, descriptors are None, predetermined is False.
id is 209, name is New Zealand English, count is 

---
<a id='PreDetermined'></a>
## Label the accents that were pre-determined 

Since its inception, Mozilla Common Voice has enabled data contributors to enter demographic age such as age, gender and accent. These associations are not validated in any way, and we don't have any indicator of how accurate they are. Accent _used_ to be represented as an a priori drop-down list, which the contributor could select from. From Common Voice v10, the data contributor can **self-describe** their accent, however, the previous accent list is still presented (so may be more frequently chosen by the data contributor). We need to be able to distinguish these accents visually to help with the exploration. 

```
"splits": {
        "accent": {
          "": 0.51,
          "canada": 0.03,
          "england": 0.08,
          "us": 0.23,
          "indian": 0.07,
          "australia": 0.03,
          "malaysia": 0,
          "newzealand": 0.01,
          "african": 0.01,
          "ireland": 0.01,
          "philippines": 0,
          "singapore": 0,
          "scotland": 0.02,
          "hongkong": 0,
          "bermuda": 0,
          "southatlandtic": 0,
          "wales": 0,
          "other": 0.01
        },

```

The `cv-datasets` splits above have labels for the accents that don't actually match the accent name in the data. So we need to specify the accents that are pre-determined. This is how they appear to the data contributor filling out their profile at: [https://commonvoice.mozilla.org/en/profile/info](https://commonvoice.mozilla.org/en/profile/info)


![Accents as specified on Mozilla Common Voice profile](cv-profile-specify-accent.png)


In [23]:
# create a list of the pre-existing accents 
# this is how they are given in the dataset. 

# TODO: for better maintainability, move this to a list of accents for each language, 
# that can be updated in a separate file, rather than specified here in an adhoc way. 

predetermined_accents_list = ['United States English', 
                         'England English', 
                         'India and South Asia (India, Pakistan, Sri Lanka)', 
                         'Canadian English', 
                         'Australian English', 
                         'Southern African (South Africa, Zimbabwe, Namibia)', 
                         'Irish English', 
                         'Scottish English', 
                         'New Zealand English', 
                         'Hong Kong English', 
                         'Filipino', 
                         'Malaysian English', 
                         'Singaporean English', 
                         'Welsh English', 
                         'West Indies and Bermuda (Bahamas, Bermuda, Jamaica, Trinidad)', 
                         'South Atlantic (Falkland Islands, Saint Helena)']



  

In [24]:
# use the predetermined_accents_list to populate the 'predetermined_status' attribute of each Accent object 
# to do this we use a method on the AccentCollection class

import cvaccents as cva
#reload(cva)

all_accents.updatePredeterminedStatus(predetermined_accents_list, True)

print(all_accents)


(1, <cvaccents.Accent object at 0x7f53d22f3a00>)
1
changed  id is 1, name is England English, count is 2346, locale is en, descriptors are None, predetermined is True. status to  True
(2, <cvaccents.Accent object at 0x7f53d22f3d30>)
2
changed  id is 2, name is United States English, count is 7537, locale is en, descriptors are None, predetermined is True. status to  True
(3, <cvaccents.Accent object at 0x7f53d22f3dc0>)
3
changed  id is 3, name is Hong Kong English, count is 132, locale is en, descriptors are None, predetermined is True. status to  True
(7, <cvaccents.Accent object at 0x7f53d22f35e0>)
7
(9, <cvaccents.Accent object at 0x7f53d22f3fd0>)
9
changed  id is 9, name is Australian English, count is 665, locale is en, descriptors are None, predetermined is True. status to  True
(12, <cvaccents.Accent object at 0x7f53ce889190>)
12
(15, <cvaccents.Accent object at 0x7f53ce889220>)
15
changed  id is 15, name is Southern African (South Africa, Zimbabwe, Namibia), count is 261, local

---
<a id='AccentDescriptors'></a>

## Create Accent Descriptors and add them to each Accent 

Each Accent can have multiple Accent Descriptors. 

For example the accent `Pronounced German` contains both a _national regional descriptor_ and an _accent strength descriptor_. 

I have used the following principles for Accent Descriptors for English. This should be considered a CodeBook. 

### Geographic Regional Descriptors 

Regional descriptors are where the accent has been specified with reference to a geographic region. 

* `Geographic Region` 

Within this Category, there are several sub-categories: 

* `Country Descriptor` - where the descriptor is a country or a nation-state. 
* `Supranational region descriptor` - where the descriptor is a geographic region that crosses or overlaps multiple countries. An example would be `Slavic`, which refers to an [ethno-linguistic group](https://en.wikipedia.org/wiki/Slavic_languages) that covers several countries in Eastern Europe. 
* `Subnational region descriptor` - where the descriptor is a geographic region that refers to a region within a country's national boundary. An example would be `Midwestern United States`. 
* `City descriptor` - where the descriptor is a geographic region that refers to a city, town or municipality. An example would be `New York City` or `London`. 

One choice I have made here is not to represent areas _within_ cities using a separate Accent Descriptor. Examples here would be `Brooklyn` or `East London` - they have been classified as cities. This is because there are so few of them that it doesn't change the analysis significantly. 

### First or other language descriptor

This refers to Accent Descriptors where the data contributor refers to their accent using a descriptor such as `non-native` or `native speaker`. This is sometimes referred to as `first language (L1)` or `second language (L2)`. Although this _may_ be used to refer to the data contributor's _level of fluency_ in a language, I've chosen not to refer to this as a _level of fluency_ - because even though someone speaks a language as a second or other language, this _does not imply_ their level of fluency specifically. One could speak Mandarin as a second language, but be highly fluent. One could speak French as a second language and be less than proficient. 

* `First or other language` 

### Accent strength descriptor 

This refers to Accent Descriptors where the data contributor refers to their accent using a marker of the strength of the accent. Examples included `pronounced`, `90%` or `slight`. 

* `Accent strength descriptor` 

### Vocal quality descriptor 

This refers to Accent Descriptors where the data contributor refers to their accent using words to describe aspects of their voice that are subjective and qualitative - such as `sultry` or `sassy`. 

* `Vocal quality descriptor` 

TODO: is `quality` the correct word here? 

## Phonetic changes 

This category refers to Accent Descriptors which describe a particular phonetic change. This is used as a parent category to group these Accent Descriptors. 

* `Phonetic changes`

### Specific phonetic changes 

There are several phonetic changes that are linguistic markers for accent difference. 

* `Specified phonetic change` is applied when the Accent Descriptor itself specifies the type of phonetic change. `cot-caught merger` is an example. 

* `Rhoticity` is applied when the Accent Descriptor is describing how `/r/` and related phonemes are pronounced.

* `Inflection` is applied when the Accent Descriptor is describing an inflection change. 

## Register 

Although the Mozilla Common Voice data used _elicited speech_ - utterances spoken from given text prompts, people can speak in a range of _registers_. A register is generally the level of formality of speech - such as `formal`, or `educated` or `slang`. It may indicate socio-economic heritage of the speaker. This category captures Accent Descriptors that describe an accent in this way. 

* `Register` 

## Named accent 

Some accents, such as `Geordie` or `Scouse` have a related geographical region descriptor - North East England, and Liverpool respectively, but ones such as `Received Pronunciation` do not. This category allows for having a Named Accent descriptor where no related geographic region descriptor exists, as well as being able to capture specifically named accents.

* `Named Accent`

## Accent effects due to physical changes 

Accent changes may occur due to physical changes in the speaker's vocal tract - for instance through surgery or disease. This Accent Descriptor is used to capture descriptions such as these. 

* `Accent effects due to physical changes`

## Mixed or variable accent 

Where the data contributor specifies that their accent is a mixture or amalgamation of accents, but does not provide further information (for example so the Accent Descriptors can be separated or merged), this Accent Descriptor is used to capture this description. 

* `Mixed or variable accent`






In [25]:
import cvaccents as cva
#reload(cva)

# Using the Accent Descriptor class to create Accent Descriptor accents for the above 

descriptorGeoRegion = cva.AccentDescriptor(
    id = 100, 
    name='Geographic region', 
    definition = 'Indicates a geographic region used as a descriptor.', 
    parent = None, 
)
descriptorGeoCountry = cva.AccentDescriptor(
    id = 200, 
    name='Country', 
    definition = 'Indicates a geographic region of a country or nation-state.', 
    parent = 100, 
)
descriptorGeoSupra = cva.AccentDescriptor(
    id = 300, 
    name='Supranational region', 
    definition = 'Indicates a geographic region which crosses or overlaps multiple countries.', 
    parent = 100, 
)
descriptorGeoSub = cva.AccentDescriptor(
    id = 400, 
    name='Subnational region', 
    definition = 'Indicates a geographic region within a national boundary.', 
    parent = 100, 
)
descriptorGeoCity = cva.AccentDescriptor(
    id = 500, 
    name='City', 
    definition = 'Indicates a geographic region referring to a city, town or municipality.', 
    parent = 100, 
)


descriptorFOL = cva.AccentDescriptor(
    id = 600, 
    name='First or other language', 
    definition = 'Indicates a descriptor related to whether this is the speaker\s first or other language.', 
    parent = None, 
)

descriptorAccStr = cva.AccentDescriptor(
    id = 700, 
    name='Accent strength descriptor', 
    definition = 'Indicates a marker of accent strength.', 
    parent = None, 
)

descriptorVocQual = cva.AccentDescriptor(
    id = 800, 
    name='Vocal quality descriptor', 
    definition = 'Indicates a subjective vocal quality.', 
    parent = None, 
)


descriptorPhonChanges = cva.AccentDescriptor(
    id = 1000, 
    name='Phonetic Changes', 
    definition = 'Indicates a phonetic change.', 
    parent = None, 
)
descriptorPhonSpecific = cva.AccentDescriptor(
    id = 1100, 
    name='Specific phonetic changes', 
    definition = 'Indicates a specific phonetic change.', 
    parent = 1000, 
)
descriptorPhonRhoticity = cva.AccentDescriptor(
    id = 1200, 
    name='Rhoticity', 
    definition = 'Indicates rhoticity or its absence.', 
    parent = 1000, 
)
descriptorPhonInflection = cva.AccentDescriptor(
    id = 1200, 
    name='Inflection', 
    definition = 'Indicates an inflection change.', 
    parent = 1000, 
)

descriptorRegister = cva.AccentDescriptor(
    id = 1300, 
    name='Register', 
    definition = 'Indicates which register the data contributor speaks in.', 
    parent = None, 
)

descriptorNamedAcc = cva.AccentDescriptor(
    id = 1400, 
    name='Specifically named accent', 
    definition = 'Indicates a specifically named accent.', 
    parent = None, 
)

descriptorPhysChange = cva.AccentDescriptor(
    id = 1500, 
    name='Accent effects due to physical changes', 
    definition = 'Indicates accent changes due to physical changes of the data contributor.', 
    parent = None, 
)

descriptorAccMixed = cva.AccentDescriptor(
    id = 1600, 
    name='Mixed or variable accent', 
    definition = 'Indicates mixture or amalgamation of accents.', 
    parent = None, 
)


descriptorAccUncertainty = cva.AccentDescriptor(
    id = 2000, 
    name='Uncertainty marker', 
    definition = 'Indicates uncertainty of descriptor.', 
    parent = None, 
)


print(descriptorGeoRegion.__str__())
print(descriptorGeoCountry.__str__())
print(descriptorGeoSupra.__str__())
print(descriptorGeoSub.__str__())
print(descriptorGeoCity.__str__())

print(descriptorFOL.__str__())

print(descriptorAccStr.__str__())

print(descriptorVocQual.__str__())

print(descriptorPhonChanges.__str__())
print(descriptorPhonSpecific.__str__())
print(descriptorPhonRhoticity.__str__())
print(descriptorPhonInflection.__str__())

print(descriptorRegister.__str__())

print(descriptorNamedAcc.__str__())

print(descriptorPhysChange.__str__())

print(descriptorAccMixed.__str__())

import cvaccents as cva
#reload(cva)

# Using the Accent Descriptor class to create Accent Descriptor accents for the above 

descriptorGeoRegion = cva.AccentDescriptor(
    id = 100, 
    name='Geographic region', 
    definition = 'Indicates a geographic region used as a descriptor.', 
    parent = None, 
)
descriptorGeoCountry = cva.AccentDescriptor(
    id = 200, 
    name='Country', 
    definition = 'Indicates a geographic region of a country or nation-state.', 
    parent = 100, 
)
descriptorGeoSupra = cva.AccentDescriptor(
    id = 300, 
    name='Supranational region', 
    definition = 'Indicates a geographic region which crosses or overlaps multiple countries.', 
    parent = 100, 
)
descriptorGeoSub = cva.AccentDescriptor(
    id = 400, 
    name='Subnational region', 
    definition = 'Indicates a geographic region within a national boundary.', 
    parent = 100, 
)
descriptorGeoCity = cva.AccentDescriptor(
    id = 500, 
    name='City', 
    definition = 'Indicates a geographic region referring to a city, town or municipality.', 
    parent = 100, 
)


descriptorFOL = cva.AccentDescriptor(
    id = 600, 
    name='First or other language', 
    definition = 'Indicates a descriptor related to whether this is the speaker\s first or other language.', 
    parent = None, 
)

descriptorAccStr = cva.AccentDescriptor(
    id = 700, 
    name='Accent strength descriptor', 
    definition = 'Indicates a marker of accent strength.', 
    parent = None, 
)

descriptorVocQual = cva.AccentDescriptor(
    id = 800, 
    name='Vocal quality descriptor', 
    definition = 'Indicates a subjective vocal quality.', 
    parent = None, 
)


descriptorPhonChanges = cva.AccentDescriptor(
    id = 1000, 
    name='Phonetic Changes', 
    definition = 'Indicates a phonetic change.', 
    parent = None, 
)
descriptorPhonSpecific = cva.AccentDescriptor(
    id = 1100, 
    name='Specific phonetic changes', 
    definition = 'Indicates a specific phonetic change.', 
    parent = 1000, 
)
descriptorPhonRhoticity = cva.AccentDescriptor(
    id = 1200, 
    name='Rhoticity', 
    definition = 'Indicates rhoticity or its absence.', 
    parent = 1000, 
)
descriptorPhonInflection = cva.AccentDescriptor(
    id = 1200, 
    name='Inflection', 
    definition = 'Indicates an inflection change.', 
    parent = 1000, 
)

descriptorRegister = cva.AccentDescriptor(
    id = 1300, 
    name='Register', 
    definition = 'Indicates which register the data contributor speaks in.', 
    parent = None, 
)

descriptorNamedAcc = cva.AccentDescriptor(
    id = 1400, 
    name='Named Accent', 
    definition = 'Indicates a specifically named accent.', 
    parent = None, 
)

descriptorPhysChange = cva.AccentDescriptor(
    id = 1500, 
    name='Accent effects due to physical changes', 
    definition = 'Indicates accent changes due to physical changes of the data contributor.', 
    parent = None, 
)

descriptorAccMixed = cva.AccentDescriptor(
    id = 1600, 
    name='Mixed or variable accent', 
    definition = 'Indicates mixture or amalgamation of accents.', 
    parent = None, 
)


descriptorAccUncertainty = cva.AccentDescriptor(
    id = 2000, 
    name='Uncertainty marker', 
    definition = 'Indicates uncertainty of descriptor.', 
    parent = None, 
)


print(descriptorGeoRegion.__str__())
print(descriptorGeoCountry.__str__())
print(descriptorGeoSupra.__str__())
print(descriptorGeoSub.__str__())
print(descriptorGeoCity.__str__())

print(descriptorFOL.__str__())

print(descriptorAccStr.__str__())

print(descriptorVocQual.__str__())

print(descriptorPhonChanges.__str__())
print(descriptorPhonSpecific.__str__())
print(descriptorPhonRhoticity.__str__())
print(descriptorPhonInflection.__str__())

print(descriptorRegister.__str__())

print(descriptorNamedAcc.__str__())

print(descriptorPhysChange.__str__())

print(descriptorAccMixed.__str__())

print(descriptorAccUncertainty.__str__())









id is 100, name is Geographic region, definition is Indicates a geographic region used as a descriptor., parent is None
id is 200, name is Country, definition is Indicates a geographic region of a country or nation-state., parent is 100
id is 300, name is Supranational region, definition is Indicates a geographic region which crosses or overlaps multiple countries., parent is 100
id is 400, name is Subnational region, definition is Indicates a geographic region within a national boundary., parent is 100
id is 500, name is City, definition is Indicates a geographic region referring to a city, town or municipality., parent is 100
id is 600, name is First or other language, definition is Indicates a descriptor related to whether this is the speaker\s first or other language., parent is None
id is 700, name is Accent strength descriptor, definition is Indicates a marker of accent strength., parent is None
id is 800, name is Vocal quality descriptor, definition is Indicates a subjective voc

### Now we have the Accent Descriptors defined, we can associate Accent Descriptors with each Accent 

In [26]:
# I could put them all in one list, 
# but it's easier to debug this way

# Generic region descriptors that don't fit into any other category 
region_descriptors = [
    ('non regional', descriptorGeoRegion),
    ('International English', descriptorFOL)
]

# Country descriptors 
country_descriptors = [ 
    ('England English', descriptorGeoCountry),
    ('United States English', descriptorGeoCountry),
    ('Hong Kong English', descriptorGeoCountry),
    ('Australian English', descriptorGeoCountry),
    ('French', descriptorGeoCountry),
    ('Colombian', descriptorGeoCountry),
    ('Canadian English', descriptorGeoCountry),
    ('Scottish English', descriptorGeoCountry),
    ('Filipino', descriptorGeoCountry),
    ('Argentinian English', descriptorGeoCountry),
    ('Finnish', descriptorGeoCountry),
    ('Singaporean English', descriptorGeoCountry),
    ('Georgian English', descriptorGeoCountry),
    ('New Zealand English', descriptorGeoCountry),
    ('Malaysian English', descriptorGeoCountry),
    ('Irish English', descriptorGeoCountry),
    ('Chinese', descriptorGeoCountry),
    ('Nigerian', descriptorGeoCountry),
    ('Ukrainian', descriptorGeoCountry),
    ('Polish', descriptorGeoCountry),
    ('Romanian', descriptorGeoCountry),
    ('Welsh English', descriptorGeoCountry),
    ('British', descriptorGeoCountry),
    ('German', descriptorGeoCountry),
    ('Swedish', descriptorGeoCountry),
    ('Spanish', descriptorGeoCountry),
    ('Japanese', descriptorGeoCountry),
    ('Israeli', descriptorGeoCountry),
    ('Dutch', descriptorGeoCountry),
    ('Russian', descriptorGeoCountry),
    ('Northern Irish', descriptorGeoCountry),
    ('Greek', descriptorGeoCountry),
    ('Kenyan', descriptorGeoCountry),
    ('Bangladeshi', descriptorGeoCountry),
    ('Norwegian', descriptorGeoCountry),
    ('Kiwi', descriptorGeoCountry),
    ('Swiss', descriptorGeoCountry),
    ('Serbian', descriptorGeoCountry),
    ('Thai', descriptorGeoCountry),
    ('Italian', descriptorGeoCountry),
    ('Indonesian English', descriptorGeoCountry),
    ('Austrian', descriptorGeoCountry)
]

# Subnational descriptors 
subnational_descriptors = [
    ('California', descriptorGeoSub),
    ('Midlands English', descriptorGeoSub),
    ('Northern California', descriptorGeoSub),
    ('Durham', descriptorGeoSub),
    ('Catalan', descriptorGeoSub),
    ('Silicon Valley', descriptorGeoSub),
    ('Swiss German', descriptorGeoSub),
    ('Northern England', descriptorGeoSub),
    ('Southern United States', descriptorGeoSub),
    ('South Texas', descriptorGeoSub),
    ('West Indian', descriptorGeoSub),
    ('Northern', descriptorGeoSub),
    ('Southern Appalachian English', descriptorGeoSub),
    ('Southern United States English', descriptorGeoSub),
    ('Pacific Northwest', descriptorGeoSub),
    ('Southern Texas Accent', descriptorGeoSub),
    ('Midwest United States', descriptorGeoSub),
    ('Afrikaans English', descriptorGeoSub),
    ('East Ukrainian', descriptorGeoSub),
    ('Southern England', descriptorGeoSub),
    ('Yorkshire', descriptorGeoSub),
    ('East Indian', descriptorGeoSub),
    ('clickme', descriptorGeoSub),
    ('Pennsylvania', descriptorGeoSub),
    ('Middle eastern seaboard Australian', descriptorGeoSub),
    ('Lancashire', descriptorGeoSub),
    ('Essex', descriptorGeoSub),
    ('"Valley Girl" English', descriptorGeoSub),
    ('Texas', descriptorGeoSub),
    ('New England', descriptorGeoSub),
    ('East coast', descriptorGeoSub),
    ('Okie', descriptorGeoSub),
    ('South German', descriptorGeoSub),
    ('Upper Midwestern', descriptorGeoSub),
    ('Mid-atlantic United States', descriptorGeoSub),
    ('Michigan', descriptorGeoSub),
    ('Javanese', descriptorGeoSub),
    ('Philadelphia', descriptorGeoSub),
    ('Sussex', descriptorGeoSub),
    ('New York', descriptorGeoSub),
    ('Alemannic German Accent', descriptorGeoSub),
    ('South West German', descriptorGeoSub),
    ('Southern California', descriptorGeoSub),
    ('Southwestern United States English', descriptorGeoSub),
    ('Northumbrian British English', descriptorGeoSub),
    ('Minnesotan', descriptorGeoSub)
]

# Supranational descriptors 
supranational_descriptors = [
    ('Wolof', descriptorGeoSupra),
    ('Latino', descriptorGeoSupra),
    ('Southern African (South Africa, Zimbabwe, Namibia)', descriptorGeoSupra),
    ('India and South Asia (India, Pakistan, Sri Lanka)', descriptorGeoSupra),
    ("A'lo", descriptorGeoSupra),
    ('West Indies and Bermuda (Bahamas, Bermuda, Jamaica, Trinidad)', descriptorGeoSupra),
    ('Indo-Canadian English', descriptorGeoSupra),
    ('European', descriptorGeoSupra),
    ('South Atlantic (Falkland Islands, Saint Helena)', descriptorGeoSupra),
    ('Slavic', descriptorGeoSupra),
    ('Eastern European', descriptorGeoSupra),
    ('Slovak', descriptorGeoSupra),
    ('West African', descriptorGeoSupra),
    ('Hmong', descriptorGeoSupra),
    ('Cantonese', descriptorGeoSupra),
    ('East African Khoja', descriptorGeoSupra)
]

# City descriptors 
city_descriptors = [
    ('New York City', descriptorGeoCity),
    ('Liverpool', descriptorGeoCity),
    ('East London', descriptorGeoCity),
    ('London', descriptorGeoCity),
    ('Pittsburgh', descriptorGeoCity),
    ('Sydney', descriptorGeoCity),
    ('Chicago', descriptorGeoCity),
    ('South London', descriptorGeoCity),
    ('Brooklyn Accent', descriptorGeoCity),
    ('New Orleans dialect', descriptorGeoCity)
]

# First or other language descriptors 
FOL_descriptors = [
    ('Non-native speaker', descriptorFOL),
    ('Bilingual', descriptorFOL),
    ('native', descriptorFOL),
    ('Second language', descriptorFOL),
    ('Basic', descriptorFOL),
    ('time spent in location', descriptorFOL),
    ('some', descriptorFOL),
    ('mid level', descriptorFOL),
    ('Spoke language when a child', descriptorFOL),
    ('fluent', descriptorFOL),
    ('Conversational', descriptorFOL),
    ('Foreign', descriptorFOL)
]


# Accent Strength descriptors
AccStr_descriptors = [
    ('pronounced', descriptorAccStr),
    ('slight', descriptorAccStr),
    ('Mild', descriptorAccStr),
    ('Not bad', descriptorAccStr),
    ('little bit', descriptorAccStr),
    ('tinge', descriptorAccStr),
    ('90%', descriptorAccStr),
    ('10%', descriptorAccStr),
    ('heavy', descriptorAccStr),
    ('little', descriptorAccStr),
    ('minor', descriptorAccStr)
]


# Vocal quality descriptors
VocQual_descriptors = [
    ('sultry', descriptorVocQual),
    ('classy', descriptorVocQual),
    ('sassy', descriptorVocQual),
    ('Slight lisp', descriptorVocQual),
    ('Slightly effeminate', descriptorVocQual),
    ('Low', descriptorVocQual),
    ('Demure', descriptorVocQual)
]


# Phonetic descriptors 
PhonSpecific_descriptors = [
    ('pin/pen merger', descriptorPhonSpecific),
    ('heavy consonants', descriptorPhonSpecific),
    ('cot-caught merger', descriptorPhonSpecific)
]
PhonRhoticity_descriptors = [
    ("pronounced r's", descriptorPhonRhoticity)
]
PhonInflection_descriptors = [
    ('mostly affecting inflection', descriptorPhonInflection)
]

# Register descriptors
Register_descriptors = [
    ('surfer', descriptorRegister),
    ('academic', descriptorRegister),
    ('Educated', descriptorRegister),
    ('formal', descriptorRegister),
    ('slang', descriptorRegister),
    ('Urban', descriptorRegister),
    ('classy', descriptorRegister),
    ('sassy', descriptorRegister),
    ('city', descriptorRegister),
    ('Cool', descriptorRegister),
    ('Conversational', descriptorRegister),
    ('Received Pronunciation', descriptorRegister)
]

# Named accent descriptors
NamedAcc_descriptors = [
    ('Patois', descriptorNamedAcc),
    ('Received Pronunciation', descriptorNamedAcc),
    ('Kiwi', descriptorNamedAcc),
    ('Chicano English', descriptorNamedAcc),
    ('"Valley Girl" English', descriptorNamedAcc),
]
        
# Physical change descriptors
PhysChange_descriptors = [
    ('changes due to oral surgery', descriptorPhysChange)
]

# Mixed accent descriptors
AccMixed_descriptors = [
    ('pronounced', descriptorAccMixed),
    ('Variable', descriptorAccMixed),
    ('Adjustable', descriptorAccMixed),
    ('Mix of accents', descriptorAccMixed),
    ('try to maintain originality', descriptorAccMixed)
]
    
# Uncertainty marker 
AccUncertainty_descriptors = [
    ('I think', descriptorAccUncertainty)
]    


In [27]:
# create one list from the above lists 

accent_descriptor_list = [
    region_descriptors,
    country_descriptors,
    subnational_descriptors,
    supranational_descriptors,
    city_descriptors,
    FOL_descriptors,
    AccStr_descriptors,
    VocQual_descriptors,
    PhonSpecific_descriptors,
    PhonRhoticity_descriptors,
    PhonInflection_descriptors,
    Register_descriptors,
    NamedAcc_descriptors,
    PhysChange_descriptors,
    AccMixed_descriptors,
    AccUncertainty_descriptors,
]



In [28]:
# Now we loop through all the accents 
# And if the accent name matches one of the descriptors in accent_descriptor_list 
# We add the relevant Accent Descriptor to the Accent's object representation 

for accent_descriptor_category in accent_descriptor_list: 
    for accent_descriptor in accent_descriptor_category: 
        for accent in all_accents.items(): 
            
            #print ('accent is: ', accent[1], ' and accent_descriptor is: ', accent_descriptor)
            
            if accent[1]._name == accent_descriptor[0]: 
                #print ('MATCH!')
                if accent[1]._descriptors is None: 
                    accent[1]._descriptors = [] # initialise list if None
                accent[1]._descriptors.append(accent_descriptor[1]) # append because there can be multiple 
                

In [29]:
# the accents should now have descriptors 

import cvaccents as cva
#reload(cva)

for accent in all_accents.items(): 
    print(accent[1].__str__())

id is 1, name is England English, count is 2346, locale is en, descriptors are [<cvaccents.AccentDescriptor object at 0x7f53d233f310>], predetermined is True.
id is 2, name is United States English, count is 7537, locale is en, descriptors are [<cvaccents.AccentDescriptor object at 0x7f53d233f310>], predetermined is True.
id is 3, name is Hong Kong English, count is 132, locale is en, descriptors are [<cvaccents.AccentDescriptor object at 0x7f53d233f310>], predetermined is True.
id is 7, name is Wolof, count is 1, locale is en, descriptors are [<cvaccents.AccentDescriptor object at 0x7f53d2340ee0>], predetermined is False.
id is 9, name is Australian English, count is 665, locale is en, descriptors are [<cvaccents.AccentDescriptor object at 0x7f53d233f310>], predetermined is True.
id is 12, name is Latino, count is 7, locale is en, descriptors are [<cvaccents.AccentDescriptor object at 0x7f53d2340ee0>], predetermined is False.
id is 15, name is Southern African (South Africa, Zimbabwe,

In [30]:
# Now do a cross-check to see if there are any accents for which the ._descriptor is None 
# this flags if I've missed an accent somewhere 



missing_descriptors = all_accents.reportNoneAccentDescriptors() 

for accent in missing_descriptors: 
    print (accent[1].__str__())
    

## Create relationships between Accents suitable for data visualisation 

Now, we want to create relationships _between_ accents so that we can visualise accents as **nodes** and their relationships as **edges**. 

In [31]:
pp.pprint(english_accents_list)

[   ['England English', 'United States English'],
    ['Hong Kong English'],
    ['England English'],
    ['United States English'],
    ['United States English', 'Wolof'],
    ['England English'],
    ['Australian English'],
    ['United States English'],
    ['United States English', 'Latino'],
    ['United States English'],
    ['United States English'],
    ['Southern African (South Africa, Zimbabwe, Namibia)'],
    ['United States English'],
    ['United States English'],
    ['India and South Asia (India, Pakistan, Sri Lanka)'],
    ['United States English'],
    ['United States English'],
    ['England English'],
    ['India and South Asia (India, Pakistan, Sri Lanka)'],
    ['England English'],
    ['United States English'],
    ['Southern African (South Africa, Zimbabwe, Namibia)'],
    ['Australian English'],
    ['England English'],
    ['India and South Asia (India, Pakistan, Sri Lanka)'],
    ['United States English'],
    ['United States English', 'Colombian'],
    ['Indi

In [32]:
for idx, value in all_accents.items(): 
    print(idx, value)

1 id is 1, name is England English, count is 2346, locale is en, descriptors are [<cvaccents.AccentDescriptor object at 0x7f53d233f310>], predetermined is True.
2 id is 2, name is United States English, count is 7537, locale is en, descriptors are [<cvaccents.AccentDescriptor object at 0x7f53d233f310>], predetermined is True.
3 id is 3, name is Hong Kong English, count is 132, locale is en, descriptors are [<cvaccents.AccentDescriptor object at 0x7f53d233f310>], predetermined is True.
7 id is 7, name is Wolof, count is 1, locale is en, descriptors are [<cvaccents.AccentDescriptor object at 0x7f53d2340ee0>], predetermined is False.
9 id is 9, name is Australian English, count is 665, locale is en, descriptors are [<cvaccents.AccentDescriptor object at 0x7f53d233f310>], predetermined is True.
12 id is 12, name is Latino, count is 7, locale is en, descriptors are [<cvaccents.AccentDescriptor object at 0x7f53d2340ee0>], predetermined is False.
15 id is 15, name is Southern African (South A

In [33]:
## Creating linkages between the individual accents and how they are represented in the data. 
## What I want to do here is create a data structure that has the ID of the accent 
## and something to describe the edge: 
## 
## The data structure I think will work here is: 
## 
## { 99: (123, 456)} 
## to represent an edge between accent ID 123 and accent 456
## 
## One thing to be aware of here is that the edges are NON-DIRECTIONAL
## {99: (123, 456)}
## is equivalent to 
## {99: (123, 456)}
## so we need a way to remove duplicates 

## The data structures we are using are: 
## 
## all_accents - Accent Collection object of all Accents, merged and normalised
## english_accents_list - this is a list of list of strings,
##                        where each list represents the Accents that are related
##   
## what we want to do is go through each list, 
## and find the ID number of the accent 
## from the Dict, 
## then build a Dict that represents the Accent's relation to other Accents
## this is accent_nodes

accent_nodes = {}
i = 0;

for accent_list in english_accents_list:

    #print(accent_list)
    
    # initialise the list first 
    accent_nodes[i] = []
    
    for accent_list_item in accent_list: 
        #print('now processing', accent_list_item)
        
        for accent in all_accents.items(): 
            
            #if (i%ratio_display ==0): # only show the 100th 
                #print('---')
                #print ('now looking at row: ', accent_list, 'and accent list item: ', accent_list_item, ' and accent: ', accent)
        
            if (accent_list_item == accent[1]._name): ## match 
                
                #if (i%ratio_display ==0): # only show the 100th 
                    #print('---')
                    #print ('match!')
                    
                #print(accent[0])
                #print('i is: ', i)
                
                
                accent_nodes[i].append(accent[0]) # we want the accent ID number
                
                if (len(accent_nodes[i]) > 1) : 
                    # double check nodes that have more than 1 element 
                    print(accent[0])
                    print('i is: ', i)
                    print('length of accent_nodes[i] is: ', len(accent_nodes[i]))
                    pp.pprint(accent_nodes[i])
                

    
    
     
    i +=1                 

2
i is:  0
length of accent_nodes[i] is:  2
[1, 2]
7
i is:  4
length of accent_nodes[i] is:  2
[2, 7]
12
i is:  8
length of accent_nodes[i] is:  2
[2, 12]
31
i is:  26
length of accent_nodes[i] is:  2
[2, 31]
59
i is:  53
length of accent_nodes[i] is:  2
[58, 59]
18
i is:  126
length of accent_nodes[i] is:  2
[2, 18]
1
i is:  139
length of accent_nodes[i] is:  2
[18, 1]
37
i is:  191
length of accent_nodes[i] is:  2
[2, 37]
18
i is:  191
length of accent_nodes[i] is:  3
[2, 37, 18]
277
i is:  266
length of accent_nodes[i] is:  2
[2, 277]
335
i is:  323
length of accent_nodes[i] is:  2
[1, 335]
2
i is:  406
length of accent_nodes[i] is:  2
[18, 2]
1
i is:  419
length of accent_nodes[i] is:  2
[2, 1]
472
i is:  457
length of accent_nodes[i] is:  2
[471, 472]
489
i is:  473
length of accent_nodes[i] is:  2
[58, 489]
490
i is:  473
length of accent_nodes[i] is:  3
[58, 489, 490]
2
i is:  528
length of accent_nodes[i] is:  2
[9, 2]
3
i is:  602
length of accent_nodes[i] is:  2
[1, 3]
2
i is

2
i is:  7099
length of accent_nodes[i] is:  2
[1, 2]
669
i is:  7141
length of accent_nodes[i] is:  2
[7297, 669]
4341
i is:  7141
length of accent_nodes[i] is:  3
[7297, 669, 4341]
7300
i is:  7141
length of accent_nodes[i] is:  4
[7297, 669, 4341, 7300]
7477
i is:  7317
length of accent_nodes[i] is:  2
[2, 7477]
7478
i is:  7317
length of accent_nodes[i] is:  3
[2, 7477, 7478]
490
i is:  7376
length of accent_nodes[i] is:  2
[7537, 490]
1016
i is:  7376
length of accent_nodes[i] is:  3
[7537, 490, 1016]
1325
i is:  7469
length of accent_nodes[i] is:  2
[2, 1325]
1
i is:  7490
length of accent_nodes[i] is:  2
[9, 1]
1106
i is:  7508
length of accent_nodes[i] is:  2
[2, 1106]
7744
i is:  7577
length of accent_nodes[i] is:  2
[2, 7744]
258
i is:  7588
length of accent_nodes[i] is:  2
[134, 258]
7771
i is:  7602
length of accent_nodes[i] is:  2
[2, 7771]
489
i is:  7635
length of accent_nodes[i] is:  2
[4069, 489]
302
i is:  7782
length of accent_nodes[i] is:  2
[37, 302]
7992
i is:  78

In [34]:
pp.pprint(len(accent_nodes))

14822


In [35]:
pp.pprint(accent_nodes)

{   0: [1, 2],
    1: [3],
    2: [1],
    3: [2],
    4: [2, 7],
    5: [1],
    6: [9],
    7: [2],
    8: [2, 12],
    9: [2],
    10: [2],
    11: [15],
    12: [2],
    13: [2],
    14: [18],
    15: [2],
    16: [2],
    17: [1],
    18: [18],
    19: [1],
    20: [2],
    21: [15],
    22: [9],
    23: [1],
    24: [18],
    25: [2],
    26: [2, 31],
    27: [18],
    28: [18],
    29: [2],
    30: [2],
    31: [18],
    32: [37],
    33: [2],
    34: [18],
    35: [18],
    36: [2],
    37: [18],
    38: [2],
    39: [3],
    40: [2],
    41: [1],
    42: [1],
    43: [2],
    44: [1],
    45: [2],
    46: [1],
    47: [15],
    48: [2],
    49: [1],
    50: [2],
    51: [1],
    52: [2],
    53: [58, 59],
    54: [2],
    55: [18],
    56: [18],
    57: [2],
    58: [18],
    59: [9],
    60: [18],
    61: [18],
    62: [2],
    63: [1],
    64: [70],
    65: [2],
    66: [18],
    67: [2],
    68: [18],
    69: [2],
    70: [2],
    71: [2],
    72: [1],
    73: [79],
    74:

    5965: [37],
    5966: [18],
    5967: [2],
    5968: [9],
    5969: [2],
    5970: [2],
    5971: [209],
    5972: [2],
    5973: [2],
    5974: [2],
    5975: [2],
    5976: [2],
    5977: [2],
    5978: [2],
    5979: [1],
    5980: [2],
    5981: [18],
    5982: [1],
    5983: [2],
    5984: [209],
    5985: [2],
    5986: [37],
    5987: [140],
    5988: [1],
    5989: [37],
    5990: [2],
    5991: [1],
    5992: [2],
    5993: [18],
    5994: [37],
    5995: [1],
    5996: [37],
    5997: [209],
    5998: [9],
    5999: [37],
    6000: [37],
    6001: [2],
    6002: [2],
    6003: [18],
    6004: [2],
    6005: [2],
    6006: [9],
    6007: [2],
    6008: [37],
    6009: [2],
    6010: [2],
    6011: [2],
    6012: [18],
    6013: [18],
    6014: [9],
    6015: [37],
    6016: [2],
    6017: [2],
    6018: [2],
    6019: [134],
    6020: [18],
    6021: [2],
    6022: [2],
    6023: [2],
    6024: [2],
    6025: [1],
    6026: [9],
    6027: [2],
    6028: [18],
    6029: [18

    8286: [2],
    8287: [37],
    8288: [37],
    8289: [1],
    8290: [2],
    8291: [2],
    8292: [134],
    8293: [2],
    8294: [1],
    8295: [2],
    8296: [2],
    8297: [2],
    8298: [2],
    8299: [2],
    8300: [2],
    8301: [2],
    8302: [1],
    8303: [258],
    8304: [18],
    8305: [1],
    8306: [2],
    8307: [2],
    8308: [2],
    8309: [70],
    8310: [18],
    8311: [1],
    8312: [2],
    8313: [1],
    8314: [9],
    8315: [37],
    8316: [2],
    8317: [37],
    8318: [2],
    8319: [18],
    8320: [9],
    8321: [1],
    8322: [2],
    8323: [2],
    8324: [2],
    8325: [18],
    8326: [2],
    8327: [37],
    8328: [1],
    8329: [2],
    8330: [18],
    8331: [2],
    8332: [302],
    8333: [2],
    8334: [2],
    8335: [18],
    8336: [1],
    8337: [2],
    8338: [9],
    8339: [15],
    8340: [1],
    8341: [18],
    8342: [481],
    8343: [2],
    8344: [2],
    8345: [2],
    8346: [37],
    8347: [1],
    8348: [2],
    8349: [2],
    8350: [2],
  

    9800: [1],
    9801: [1],
    9802: [37],
    9803: [18],
    9804: [18],
    9805: [9],
    9806: [2],
    9807: [2],
    9808: [18],
    9809: [2],
    9810: [9],
    9811: [1],
    9812: [1],
    9813: [2],
    9814: [2],
    9815: [2],
    9816: [18],
    9817: [18],
    9818: [2],
    9819: [2],
    9820: [37],
    9821: [258],
    9822: [1],
    9823: [2],
    9824: [2],
    9825: [2],
    9826: [2],
    9827: [9],
    9828: [2],
    9829: [2],
    9830: [2],
    9831: [2],
    9832: [18],
    9833: [2],
    9834: [2],
    9835: [37],
    9836: [2],
    9837: [258],
    9838: [1],
    9839: [9],
    9840: [302],
    9841: [2],
    9842: [2],
    9843: [2],
    9844: [37],
    9845: [1],
    9846: [15],
    9847: [18],
    9848: [1],
    9849: [2],
    9850: [2],
    9851: [18],
    9852: [1],
    9853: [37],
    9854: [1],
    9855: [2],
    9856: [18],
    9857: [2],
    9858: [37],
    9859: [15],
    9860: [2],
    9861: [18],
    9862: [18],
    9863: [2],
    9864: [2],


In [36]:
# this figure is a cross-check - 
# it should equal the original length of accent_nodes minus the size of deletion_list
pp.pprint(len(accent_nodes))

14822


In [37]:
pp.pprint(accent_nodes)

{   0: [1, 2],
    1: [3],
    2: [1],
    3: [2],
    4: [2, 7],
    5: [1],
    6: [9],
    7: [2],
    8: [2, 12],
    9: [2],
    10: [2],
    11: [15],
    12: [2],
    13: [2],
    14: [18],
    15: [2],
    16: [2],
    17: [1],
    18: [18],
    19: [1],
    20: [2],
    21: [15],
    22: [9],
    23: [1],
    24: [18],
    25: [2],
    26: [2, 31],
    27: [18],
    28: [18],
    29: [2],
    30: [2],
    31: [18],
    32: [37],
    33: [2],
    34: [18],
    35: [18],
    36: [2],
    37: [18],
    38: [2],
    39: [3],
    40: [2],
    41: [1],
    42: [1],
    43: [2],
    44: [1],
    45: [2],
    46: [1],
    47: [15],
    48: [2],
    49: [1],
    50: [2],
    51: [1],
    52: [2],
    53: [58, 59],
    54: [2],
    55: [18],
    56: [18],
    57: [2],
    58: [18],
    59: [9],
    60: [18],
    61: [18],
    62: [2],
    63: [1],
    64: [70],
    65: [2],
    66: [18],
    67: [2],
    68: [18],
    69: [2],
    70: [2],
    71: [2],
    72: [1],
    73: [79],
    74:

    6424: [2],
    6425: [1],
    6426: [2],
    6427: [2],
    6428: [2],
    6429: [2],
    6430: [2],
    6431: [2],
    6432: [18],
    6433: [2],
    6434: [70],
    6435: [2],
    6436: [2],
    6437: [2],
    6438: [2],
    6439: [2],
    6440: [1],
    6441: [18],
    6442: [2],
    6443: [2],
    6444: [15],
    6445: [18],
    6446: [2],
    6447: [1],
    6448: [1],
    6449: [18],
    6450: [86],
    6451: [2],
    6452: [2],
    6453: [2],
    6454: [2],
    6455: [37],
    6456: [2],
    6457: [1],
    6458: [2],
    6459: [2],
    6460: [2],
    6461: [2],
    6462: [70],
    6463: [2],
    6464: [209],
    6465: [2],
    6466: [18],
    6467: [1],
    6468: [2],
    6469: [18],
    6470: [37],
    6471: [1],
    6472: [9],
    6473: [1],
    6474: [2],
    6475: [2],
    6476: [2],
    6477: [2],
    6478: [2],
    6479: [2],
    6480: [2],
    6481: [2],
    6482: [9],
    6483: [2],
    6484: [70],
    6485: [2],
    6486: [2],
    6487: [37],
    6488: [15],
    6489

    8556: [18],
    8557: [2],
    8558: [1],
    8559: [302],
    8560: [2],
    8561: [2],
    8562: [18, 3100],
    8563: [2],
    8564: [1],
    8565: [2],
    8566: [2],
    8567: [2],
    8568: [2],
    8569: [2],
    8570: [1],
    8571: [18],
    8572: [18],
    8573: [18],
    8574: [2],
    8575: [18],
    8576: [2],
    8577: [18],
    8578: [18],
    8579: [1],
    8580: [2],
    8581: [9],
    8582: [70],
    8583: [1],
    8584: [18],
    8585: [2],
    8586: [2],
    8587: [2],
    8588: [2],
    8589: [18],
    8590: [9],
    8591: [37],
    8592: [18],
    8593: [2],
    8594: [18],
    8595: [70],
    8596: [2],
    8597: [2],
    8598: [2],
    8599: [9],
    8600: [2],
    8601: [37],
    8602: [443],
    8603: [1],
    8604: [1],
    8605: [2],
    8606: [1],
    8607: [18],
    8608: [86, 2],
    8609: [2],
    8610: [1],
    8611: [15],
    8612: [2],
    8613: [2],
    8614: [2],
    8615: [258],
    8616: [86],
    8617: [18],
    8618: [2],
    8619: [2],
    

    9631: [2],
    9632: [2],
    9633: [3],
    9634: [2],
    9635: [2],
    9636: [18],
    9637: [37],
    9638: [1],
    9639: [2],
    9640: [2],
    9641: [1],
    9642: [2],
    9643: [18],
    9644: [18],
    9645: [2],
    9646: [37],
    9647: [2],
    9648: [2],
    9649: [2],
    9650: [1],
    9651: [2],
    9652: [1],
    9653: [2],
    9654: [2],
    9655: [2],
    9656: [2],
    9657: [2],
    9658: [2],
    9659: [18],
    9660: [2],
    9661: [2],
    9662: [2],
    9663: [1],
    9664: [2],
    9665: [2],
    9666: [1],
    9667: [2],
    9668: [37],
    9669: [2],
    9670: [2],
    9671: [2],
    9672: [1],
    9673: [2],
    9674: [2],
    9675: [2],
    9676: [2],
    9677: [18],
    9678: [1],
    9679: [1587],
    9680: [2],
    9681: [2],
    9682: [1],
    9683: [2],
    9684: [37],
    9685: [2],
    9686: [2],
    9687: [2],
    9688: [9],
    9689: [2],
    9690: [2],
    9691: [2],
    9692: [258],
    9693: [2],
    9694: [2],
    9695: [86],
    9696: 

    14561: [1],
    14562: [2],
    14563: [2],
    14564: [2],
    14565: [2],
    14566: [2],
    14567: [2],
    14568: [2],
    14569: [18],
    14570: [2],
    14571: [209],
    14572: [2],
    14573: [1],
    14574: [2],
    14575: [37],
    14576: [2],
    14577: [1],
    14578: [1],
    14579: [2],
    14580: [1],
    14581: [70],
    14582: [2],
    14583: [2],
    14584: [1],
    14585: [2],
    14586: [2],
    14587: [37],
    14588: [2],
    14589: [2],
    14590: [9],
    14591: [2],
    14592: [2],
    14593: [15],
    14594: [2],
    14595: [2],
    14596: [2],
    14597: [1],
    14598: [2],
    14599: [2],
    14600: [2],
    14601: [209],
    14602: [2],
    14603: [1],
    14604: [2],
    14605: [2],
    14606: [1],
    14607: [2],
    14608: [1],
    14609: [1],
    14610: [302],
    14611: [2],
    14612: [18],
    14613: [2],
    14614: [2],
    14615: [2],
    14616: [2],
    14617: [1],
    14618: [37],
    14619: [2],
    14620: [37],
    14621: [15],
    14622

In [38]:
# Now what I need to do is create a JSON format suitable for using in 
# a Trellis diagram in Observable 
# e.g. https://observablehq.com/@jameslaneconkling/trellis

# The format of the JSON looks like: 
#   const nodes = [
#    {id: 'Myriel', group: 1},
#    {id: 'Napoleon', group: 1},

# const edges = [
#    {source: 'Napoleon', target: 'Myriel'},
#    {source: 'Mlle.Baptistine', target: 'Myriel'},

# the nodes should be as easy as JSON dumping the all_accents AccentCollection 
# possibly using a method 

# the edges will be a bit more complex 

### Nodes

In [39]:
print(all_accents.total())

165


In [40]:
#reload(cva)
all_accents.exportJSON('all_accents.json')

True

In [41]:
print(len(accent_nodes))

14822


In [42]:
pp.pprint(accent_nodes)

{   0: [1, 2],
    1: [3],
    2: [1],
    3: [2],
    4: [2, 7],
    5: [1],
    6: [9],
    7: [2],
    8: [2, 12],
    9: [2],
    10: [2],
    11: [15],
    12: [2],
    13: [2],
    14: [18],
    15: [2],
    16: [2],
    17: [1],
    18: [18],
    19: [1],
    20: [2],
    21: [15],
    22: [9],
    23: [1],
    24: [18],
    25: [2],
    26: [2, 31],
    27: [18],
    28: [18],
    29: [2],
    30: [2],
    31: [18],
    32: [37],
    33: [2],
    34: [18],
    35: [18],
    36: [2],
    37: [18],
    38: [2],
    39: [3],
    40: [2],
    41: [1],
    42: [1],
    43: [2],
    44: [1],
    45: [2],
    46: [1],
    47: [15],
    48: [2],
    49: [1],
    50: [2],
    51: [1],
    52: [2],
    53: [58, 59],
    54: [2],
    55: [18],
    56: [18],
    57: [2],
    58: [18],
    59: [9],
    60: [18],
    61: [18],
    62: [2],
    63: [1],
    64: [70],
    65: [2],
    66: [18],
    67: [2],
    68: [18],
    69: [2],
    70: [2],
    71: [2],
    72: [1],
    73: [79],
    74:

    3795: [2],
    3796: [2],
    3797: [2],
    3798: [18],
    3799: [18],
    3800: [2],
    3801: [2],
    3802: [3],
    3803: [18],
    3804: [2],
    3805: [1],
    3806: [2],
    3807: [2],
    3808: [18],
    3809: [18],
    3810: [2],
    3811: [2],
    3812: [2],
    3813: [511],
    3814: [18],
    3815: [18],
    3816: [2],
    3817: [15],
    3818: [18],
    3819: [258],
    3820: [2],
    3821: [2],
    3822: [2],
    3823: [258],
    3824: [2],
    3825: [2],
    3826: [1],
    3827: [9],
    3828: [2],
    3829: [3],
    3830: [2],
    3831: [2],
    3832: [1],
    3833: [18],
    3834: [2],
    3835: [2],
    3836: [18],
    3837: [2],
    3838: [1],
    3839: [2],
    3840: [2],
    3841: [18],
    3842: [18],
    3843: [18],
    3844: [9],
    3845: [1],
    3846: [2],
    3847: [2],
    3848: [2],
    3849: [2],
    3850: [2],
    3851: [2],
    3852: [2],
    3853: [2],
    3854: [1],
    3855: [1],
    3856: [1],
    3857: [1],
    3858: [18],
    3859: [70],
   

    5929: [1],
    5930: [37],
    5931: [18],
    5932: [2],
    5933: [2],
    5934: [1],
    5935: [2],
    5936: [2],
    5937: [2],
    5938: [2],
    5939: [2],
    5940: [18],
    5941: [1],
    5942: [18],
    5943: [302],
    5944: [2],
    5945: [15],
    5946: [2],
    5947: [2],
    5948: [37],
    5949: [2],
    5950: [2],
    5951: [2],
    5952: [2],
    5953: [2],
    5954: [2],
    5955: [2],
    5956: [37],
    5957: [9],
    5958: [1],
    5959: [2],
    5960: [134, 1],
    5961: [2],
    5962: [302],
    5963: [18],
    5964: [2],
    5965: [37],
    5966: [18],
    5967: [2],
    5968: [9],
    5969: [2],
    5970: [2],
    5971: [209],
    5972: [2],
    5973: [2],
    5974: [2],
    5975: [2],
    5976: [2],
    5977: [2],
    5978: [2],
    5979: [1],
    5980: [2],
    5981: [18],
    5982: [1],
    5983: [2],
    5984: [209],
    5985: [2],
    5986: [37],
    5987: [140],
    5988: [1],
    5989: [37],
    5990: [2],
    5991: [1],
    5992: [2],
    5993: [1

    7562: [302],
    7563: [18],
    7564: [2],
    7565: [18],
    7566: [302],
    7567: [37],
    7568: [1],
    7569: [134],
    7570: [2],
    7571: [2],
    7572: [1],
    7573: [2],
    7574: [9],
    7575: [18],
    7576: [2],
    7577: [2, 7744],
    7578: [2],
    7579: [2],
    7580: [86],
    7581: [2],
    7582: [1],
    7583: [18],
    7584: [18],
    7585: [2],
    7586: [2],
    7587: [37],
    7588: [134, 258],
    7589: [1],
    7590: [258],
    7591: [1],
    7592: [2],
    7593: [2],
    7594: [2],
    7595: [9],
    7596: [15],
    7597: [2],
    7598: [18],
    7599: [1],
    7600: [18],
    7601: [18],
    7602: [2, 7771],
    7603: [2],
    7604: [2],
    7605: [2841],
    7606: [2],
    7607: [2],
    7608: [70],
    7609: [18],
    7610: [2],
    7611: [37],
    7612: [18],
    7613: [2],
    7614: [18],
    7615: [2],
    7616: [15],
    7617: [18],
    7618: [2],
    7619: [37],
    7620: [2],
    7621: [1],
    7622: [2],
    7623: [2],
    7624: [9],
    7

    12381: [140],
    12382: [2],
    12383: [1],
    12384: [2],
    12385: [86],
    12386: [1],
    12387: [2],
    12388: [1],
    12389: [1],
    12390: [2],
    12391: [1],
    12392: [2],
    12393: [1],
    12394: [1],
    12395: [18],
    12396: [1],
    12397: [2],
    12398: [2],
    12399: [2],
    12400: [1],
    12401: [2],
    12402: [209],
    12403: [1],
    12404: [2],
    12405: [37],
    12406: [18],
    12407: [37],
    12408: [2],
    12409: [2],
    12410: [1],
    12411: [302],
    12412: [2],
    12413: [15],
    12414: [2],
    12415: [2],
    12416: [209],
    12417: [2],
    12418: [2],
    12419: [37],
    12420: [18],
    12421: [2],
    12422: [2],
    12423: [2],
    12424: [1],
    12425: [2],
    12426: [2],
    12427: [2],
    12428: [1],
    12429: [9],
    12430: [1],
    12431: [2],
    12432: [37],
    12433: [18],
    12434: [18],
    12435: [209],
    12436: [2],
    12437: [258],
    12438: [1],
    12439: [2],
    12440: [2],
    12441: [1],
 

    14758: [37],
    14759: [1],
    14760: [2],
    14761: [2],
    14762: [18],
    14763: [2],
    14764: [2],
    14765: [1],
    14766: [2],
    14767: [2],
    14768: [2],
    14769: [2],
    14770: [18],
    14771: [1],
    14772: [2],
    14773: [2],
    14774: [18],
    14775: [1],
    14776: [18],
    14777: [2],
    14778: [2],
    14779: [18],
    14780: [2],
    14781: [1],
    14782: [18],
    14783: [9],
    14784: [2],
    14785: [1],
    14786: [2],
    14787: [18],
    14788: [1, 209],
    14789: [18],
    14790: [18],
    14791: [18],
    14792: [2],
    14793: [2],
    14794: [1],
    14795: [2],
    14796: [2],
    14797: [1, 883, 5449],
    14798: [2],
    14799: [2],
    14800: [18],
    14801: [1],
    14802: [18],
    14803: [1],
    14804: [209],
    14805: [1],
    14806: [18],
    14807: [9],
    14808: [18],
    14809: [18],
    14810: [37],
    14811: [18],
    14812: [2],
    14813: [1719],
    14814: [2],
    14815: [70],
    14816: [1],
    14817: [9],


In [43]:
# let's do some sanity checking to make sure these are correct 

# 0: {'source': 1, 'target': 2, 'weight': 23}
# this is equivalent to the occurrence [1, 2] in accent_nodes 
# plus the occurrences of [2, 1] because we have removed bidirectional edges
# and represents a relationship between 
# 'England English' - accent id 1 - and 'United States English' - accent id 2

print('--- checking 1, 2 ---')

count = 0
for idx, node in accent_nodes.items(): 
    if (node == list([1, 2])) :
        count +=1
print(count)
        
print('--- checking 2, 1 ---')

count = 0
for idx, node in accent_nodes.items(): 
    if (node == list([2, 1])) :
        count +=1
print(count)
        
# these together should sum to 23 
# the first one is 9 which appears correct 
# but the second is 13, not 14 as expected 
# double check the values above. Why do we have an off by one error? 



print ('---')


# 139: {'source': 13016, 'target': 59, 'weight': 2}
# this is equivalent to the occurrence [13016, 59] in accent_nodes
# and represents a relationship between 
# 'Foreign' - accent id 13016 - and 'Non-native speaker'
# this didn't show originally so I dug into it. 
# The original accent listing is: 
# (12775, [750, 13016, 59])

for idx, node in accent_nodes.items(): 
    if node == list([13016, 59]) :
        print ('match')
        
# 

print ('---')

--- checking 1, 2 ---
9
--- checking 2, 1 ---
13
---
---


In [44]:
# So why am I getting an NODE count here of 13, when below I am getting an edge count of 14? 

### Edges

Here, we use the `accent_nodes` dict to create a dict of edges

In [45]:
print(len(accent_nodes))

14822


In [46]:
## what we want to do here is loop through the accent_nodes Dict 
## and create another Dict that we can use to create Links between the Nodes (which are accents)

accent_edges = {} 
accent_edges_id = 0


# make a deep copy of accent_nodes as we will be pop()ing elements off lists inside the dict 
# and if we don't make a deep copy this will affect accent_nodes as well 
# because Python uses [pass by assignment](https://docs.python.org/3/faq/programming.html#how-do-i-write-a-function-with-output-parameters-call-by-reference)

accent_nodes_for_manipulation = copy.deepcopy(accent_nodes)

for accent_list in accent_nodes_for_manipulation.items(): 
    print('\n')
    print('--- BEGIN accent list ---')
    print('accent list is: ', accent_list)
    
    if len(accent_list[1]) > 1: 
        print ('--- node has more than one accent, processing ... ---')       

        # we want to create edges, so only care where the list has two or more elements
        while (len(accent_list[1]) > 1) : 
            
            print('size of accent_list[1] BEFORE popping is: ', (len(accent_list[1])))
            popped_element = accent_list[1].pop(0) # remove the first element 
            print('popped element is :', popped_element)
            print('size of accent_list[1] AFTER popping is: ', (len(accent_list[1])))
    
            # create links between the popped element and all the remaining elements in the list 
            for accent_id in accent_list[1]: 
                
                print('\n')
                print('--- in accent list loop ---')
                print('accent_id is: ', accent_id)
                print('length of accent list is: ', len(accent_list[1]))
                
                print('popped_element inside the for loop is: ', popped_element)
                print('accent_edges_id is: ', accent_edges_id)
                
                accent_edges[accent_edges_id] = {}
                accent_edges[accent_edges_id]['source'] = popped_element
                accent_edges[accent_edges_id]['target'] = accent_id
                accent_edges[accent_edges_id]['weight'] = 1
            
                print(accent_edges[accent_edges_id])
                
                accent_edges_id +=1
                print('checking that accent_edges_id has incremented: ', accent_edges_id)
                
            print('--- END for loop ---')
        print('--- END while loop ---')       
    print('--- END accent list ---')




--- BEGIN accent list ---
accent list is:  (0, [1, 2])
--- node has more than one accent, processing ... ---
size of accent_list[1] BEFORE popping is:  2
popped element is : 1
size of accent_list[1] AFTER popping is:  1


--- in accent list loop ---
accent_id is:  2
length of accent list is:  1
popped_element inside the for loop is:  1
accent_edges_id is:  0
{'source': 1, 'target': 2, 'weight': 1}
checking that accent_edges_id has incremented:  1
--- END for loop ---
--- END while loop ---
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (1, [3])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (2, [1])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (3, [2])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (4, [2, 7])
--- node has more than one accent, processing ... ---
size of accent_list[1] BEFORE popping is:  2
popped element is : 2
size of accent_list[1] AFTER popping is:  1


--- in accent list lo

--- END accent list ---


--- BEGIN accent list ---
accent list is:  (443, [2])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (444, [2])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (445, [2])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (446, [258])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (447, [9])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (448, [2])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (449, [2])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (450, [9])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (451, [1])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (452, [18])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (453, [2])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (454, [2])
--- END accent list ---


--- BEGIN a

--- END accent list ---


--- BEGIN accent list ---
accent list is:  (1221, [2])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (1222, [18])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (1223, [2])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (1224, [2])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (1225, [18])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (1226, [18])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (1227, [2])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (1228, [2])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (1229, [1])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (1230, [2])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (1231, [2])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (1232, [70])
--- END accent list ---


accent list is:  (2838, [2])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (2839, [9])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (2840, [2])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (2841, [2])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (2842, [2])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (2843, [2])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (2844, [9])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (2845, [2])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (2846, [2])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (2847, [18])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (2848, [2])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (2849, [18])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (2850, [2

--- BEGIN accent list ---
accent list is:  (4533, [2])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (4534, [2])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (4535, [18])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (4536, [2])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (4537, [140])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (4538, [2])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (4539, [2])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (4540, [2])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (4541, [2])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (4542, [2])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (4543, [2])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (4544, [2])
--- END accent list ---


--- BEGIN accent list ---

--- END accent list ---


--- BEGIN accent list ---
accent list is:  (4902, [2])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (4903, [70])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (4904, [2])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (4905, [2])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (4906, [2])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (4907, [1])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (4908, [15])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (4909, [18])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (4910, [9])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (4911, [2])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (4912, [2])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (4913, [209])
--- END accent list ---



--- BEGIN accent list ---
accent list is:  (7540, [134])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (7541, [2])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (7542, [1])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (7543, [258])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (7544, [2])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (7545, [18])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (7546, [18])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (7547, [2])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (7548, [140])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (7549, [37])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (7550, [2])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (7551, [2])
--- END accent list ---


--- BEGIN accent 



--- BEGIN accent list ---
accent list is:  (9188, [15])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (9189, [18])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (9190, [2])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (9191, [2])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (9192, [2])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (9193, [18])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (9194, [37])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (9195, [9])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (9196, [1])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (9197, [2])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (9198, [2])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (9199, [18])
--- END accent list ---


--- BEGIN accent list

accent list is:  (9577, [2])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (9578, [2])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (9579, [2])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (9580, [2])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (9581, [2])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (9582, [258])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (9583, [2])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (9584, [2])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (9585, [1])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (9586, [9])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (9587, [18])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (9588, [1])
--- END accent list ---


--- BEGIN accent list ---
accent list is:  (9589, [

popped element is : 37
size of accent_list[1] AFTER popping is:  2


--- in accent list loop ---
accent_id is:  2
length of accent list is:  2
popped_element inside the for loop is:  37
accent_edges_id is:  295
{'source': 37, 'target': 2, 'weight': 1}
checking that accent_edges_id has incremented:  296


--- in accent list loop ---
accent_id is:  1
length of accent list is:  2
popped_element inside the for loop is:  37
accent_edges_id is:  296
{'source': 37, 'target': 1, 'weight': 1}
checking that accent_edges_id has incremented:  297
--- END for loop ---
size of accent_list[1] BEFORE popping is:  2
popped element is : 2
size of accent_list[1] AFTER popping is:  1


--- in accent list loop ---
accent_id is:  1
length of accent list is:  1
popped_element inside the for loop is:  2
accent_edges_id is:  297
{'source': 2, 'target': 1, 'weight': 1}
checking that accent_edges_id has incremented:  298
--- END for loop ---
--- END while loop ---
--- END accent list ---


--- BEGIN accent list 

In [47]:
# accent_nodes and accent_nodes_for_manipulation should NOT be equivalent 
# because list items have been pop()'d off the latter

print(len(accent_nodes))
print(len(accent_nodes_for_manipulation))
print (accent_nodes == accent_nodes_for_manipulation)

14822
14822
False


In [48]:
print(len(accent_edges))

419


In [49]:
pp.pprint(accent_edges)

{   0: {'source': 1, 'target': 2, 'weight': 1},
    1: {'source': 2, 'target': 7, 'weight': 1},
    2: {'source': 2, 'target': 12, 'weight': 1},
    3: {'source': 2, 'target': 31, 'weight': 1},
    4: {'source': 58, 'target': 59, 'weight': 1},
    5: {'source': 2, 'target': 18, 'weight': 1},
    6: {'source': 18, 'target': 1, 'weight': 1},
    7: {'source': 2, 'target': 37, 'weight': 1},
    8: {'source': 2, 'target': 18, 'weight': 1},
    9: {'source': 37, 'target': 18, 'weight': 1},
    10: {'source': 2, 'target': 277, 'weight': 1},
    11: {'source': 1, 'target': 335, 'weight': 1},
    12: {'source': 18, 'target': 2, 'weight': 1},
    13: {'source': 2, 'target': 1, 'weight': 1},
    14: {'source': 471, 'target': 472, 'weight': 1},
    15: {'source': 58, 'target': 489, 'weight': 1},
    16: {'source': 58, 'target': 490, 'weight': 1},
    17: {'source': 489, 'target': 490, 'weight': 1},
    18: {'source': 9, 'target': 2, 'weight': 1},
    19: {'source': 1, 'target': 3, 'weight': 1},
 

In [50]:
print (len(accent_nodes))

14822


In [51]:
for idx, node in accent_nodes.items(): 
    # each node is a list 
    if len(node) > 1:
        if (1 in node) and (2 in node): 
            print(node)

[1, 2]
[2, 1]
[1, 2]
[2, 1]
[1, 2]
[2, 70, 302, 1]
[2, 1, 3]
[1, 2]
[2, 1]
[2, 1]
[2, 1]
[2, 1]
[2, 1]
[2, 1, 18]
[2, 1]
[1, 2]
[2, 9, 1, 209, 18, 4939, 1736]
[1, 2]
[2, 1]
[1, 2]
[1, 2]
[2, 1, 18]
[140, 1, 70, 2]
[2, 1]
[37, 2, 1]
[2, 1]
[1, 2, 11075]
[2, 1]
[1, 2]
[2, 1]
[1, 209, 511, 9, 2, 2459]
[2, 140, 1, 12994]


In [52]:
for idx, node in accent_nodes.items(): 
    # each node is a list 
    if len(node) > 2:
        if (1 in node) and (2 in node): 
            print(node)

[2, 70, 302, 1]
[2, 1, 3]
[2, 1, 18]
[2, 9, 1, 209, 18, 4939, 1736]
[2, 1, 18]
[140, 1, 70, 2]
[37, 2, 1]
[1, 2, 11075]
[1, 209, 511, 9, 2, 2459]
[2, 140, 1, 12994]


In [53]:
for idx, node in accent_nodes.items(): 
    # each node is a list 
    if len(node) == 2:
        if (1 in node) and (2 in node): 
            print(node)

[1, 2]
[2, 1]
[1, 2]
[2, 1]
[1, 2]
[1, 2]
[2, 1]
[2, 1]
[2, 1]
[2, 1]
[2, 1]
[2, 1]
[1, 2]
[1, 2]
[2, 1]
[1, 2]
[1, 2]
[2, 1]
[2, 1]
[2, 1]
[1, 2]
[2, 1]


This actually returns 30 lines - so we may not have as many _edges_ being generated as there should be. 

There are **11** cases in `accent_nodes` where there are more than two nodes in the list. 

There are **22** cases in `accent_nodes` where there are exactly two nodes in the list. 

_Working hypothesis for this bug:_ I think what's happening here is that the `accent_edges` for nodes with more than 2 nodes are not being generated correctly. 




Now, we de-duplicate the `accent_edges` dict


In [54]:

def deduplicateDict (accent_edges):
    
    temp_edges = []
    temp_dict = {}
    temp_weights = {}

    for key, val in accent_edges.items(): 
        #print (key)
        #print (val)
        
        if val not in temp_edges: 
            
            temp_edges.append(val)
            temp_dict[key] = val 
            temp_weights[key] = 1
            
        else: # increment the weight of the edge
            # find the key to increment based on the val
            print('breakpoint 1')
            print ('finding the key to update')
            pp.pprint(temp_dict)
            print('breakpoint 2')
            
            pp.pprint(temp_dict.keys())
            pp.pprint(temp_dict.values())
            print('breakpoint 3')
            
            pp.pprint(key)
            pp.pprint(val)
            print('breakpoint 4')
            
            update_key_position = list(temp_dict.values()).index(val) 
            #this is the *position* in the dict that should be updated 
            
            print('update_key_position is: ', update_key_position)
            
            update_key = list(temp_dict.keys())[update_key_position]

            print('update_key is: ', update_key)
            
            print(list(temp_dict.keys()))
            print('breakpoint 5')
            
            pp.pprint(temp_dict[update_key])
            temp_weights[update_key] +=1 
            print('breakpoint 6')
            
    # update the weights - we can't update in the for loop above
    # otherwise the `val` won't match, because the weight: element would be compared
    for key, val in temp_dict.items():
        val['weight'] = temp_weights[key]
        
    print(type(temp_dict))
    # sort the dict by source because it's easier to do error checking 
    temp_dict = dict(sorted(temp_dict.items(), key=lambda x: x[1]['source'], reverse=False))
    print(type(temp_dict))
    return temp_dict

In [55]:
accent_edges = deduplicateDict(accent_edges)

breakpoint 1
finding the key to update
{   0: {'source': 1, 'target': 2, 'weight': 1},
    1: {'source': 2, 'target': 7, 'weight': 1},
    2: {'source': 2, 'target': 12, 'weight': 1},
    3: {'source': 2, 'target': 31, 'weight': 1},
    4: {'source': 58, 'target': 59, 'weight': 1},
    5: {'source': 2, 'target': 18, 'weight': 1},
    6: {'source': 18, 'target': 1, 'weight': 1},
    7: {'source': 2, 'target': 37, 'weight': 1}}
breakpoint 2
dict_keys([0, 1, 2, 3, 4, 5, 6, 7])
dict_values([{'source': 1, 'target': 2, 'weight': 1}, {'source': 2, 'target': 7, 'weight': 1}, {'source': 2, 'target': 12, 'weight': 1}, {'source': 2, 'target': 31, 'weight': 1}, {'source': 58, 'target': 59, 'weight': 1}, {'source': 2, 'target': 18, 'weight': 1}, {'source': 18, 'target': 1, 'weight': 1}, {'source': 2, 'target': 37, 'weight': 1}])
breakpoint 3
8
{'source': 2, 'target': 18, 'weight': 1}
breakpoint 4
update_key_position is:  5
update_key is:  5
[0, 1, 2, 3, 4, 5, 6, 7]
breakpoint 5
{'source': 2, 'targe

{   0: {'source': 1, 'target': 2, 'weight': 1},
    1: {'source': 2, 'target': 7, 'weight': 1},
    2: {'source': 2, 'target': 12, 'weight': 1},
    3: {'source': 2, 'target': 31, 'weight': 1},
    4: {'source': 58, 'target': 59, 'weight': 1},
    5: {'source': 2, 'target': 18, 'weight': 1},
    6: {'source': 18, 'target': 1, 'weight': 1},
    7: {'source': 2, 'target': 37, 'weight': 1},
    9: {'source': 37, 'target': 18, 'weight': 1},
    10: {'source': 2, 'target': 277, 'weight': 1},
    11: {'source': 1, 'target': 335, 'weight': 1},
    12: {'source': 18, 'target': 2, 'weight': 1},
    13: {'source': 2, 'target': 1, 'weight': 1},
    14: {'source': 471, 'target': 472, 'weight': 1},
    15: {'source': 58, 'target': 489, 'weight': 1},
    16: {'source': 58, 'target': 490, 'weight': 1},
    17: {'source': 489, 'target': 490, 'weight': 1},
    18: {'source': 9, 'target': 2, 'weight': 1},
    19: {'source': 1, 'target': 3, 'weight': 1},
    21: {'source': 750, 'target': 751, 'weight': 1

dict_values([{'source': 1, 'target': 2, 'weight': 1}, {'source': 2, 'target': 7, 'weight': 1}, {'source': 2, 'target': 12, 'weight': 1}, {'source': 2, 'target': 31, 'weight': 1}, {'source': 58, 'target': 59, 'weight': 1}, {'source': 2, 'target': 18, 'weight': 1}, {'source': 18, 'target': 1, 'weight': 1}, {'source': 2, 'target': 37, 'weight': 1}, {'source': 37, 'target': 18, 'weight': 1}, {'source': 2, 'target': 277, 'weight': 1}, {'source': 1, 'target': 335, 'weight': 1}, {'source': 18, 'target': 2, 'weight': 1}, {'source': 2, 'target': 1, 'weight': 1}, {'source': 471, 'target': 472, 'weight': 1}, {'source': 58, 'target': 489, 'weight': 1}, {'source': 58, 'target': 490, 'weight': 1}, {'source': 489, 'target': 490, 'weight': 1}, {'source': 9, 'target': 2, 'weight': 1}, {'source': 1, 'target': 3, 'weight': 1}, {'source': 750, 'target': 751, 'weight': 1}, {'source': 2, 'target': 763, 'weight': 1}, {'source': 2, 'target': 776, 'weight': 1}, {'source': 2, 'target': 777, 'weight': 1}, {'sour

    30: {'source': 2, 'target': 70, 'weight': 1},
    31: {'source': 2, 'target': 302, 'weight': 1},
    33: {'source': 70, 'target': 302, 'weight': 1},
    34: {'source': 70, 'target': 1, 'weight': 1},
    35: {'source': 302, 'target': 1, 'weight': 1},
    37: {'source': 2, 'target': 3, 'weight': 1},
    42: {'source': 669, 'target': 1015, 'weight': 1},
    43: {'source': 669, 'target': 1016, 'weight': 1},
    44: {'source': 1015, 'target': 1016, 'weight': 1},
    45: {'source': 1059, 'target': 1060, 'weight': 1},
    46: {'source': 1, 'target': 59, 'weight': 1},
    47: {'source': 1, 'target': 1083, 'weight': 1},
    48: {'source': 1, 'target': 1084, 'weight': 1},
    49: {'source': 1083, 'target': 1084, 'weight': 1},
    51: {'source': 1140, 'target': 490, 'weight': 1},
    52: {'source': 1140, 'target': 1142, 'weight': 1},
    53: {'source': 490, 'target': 1142, 'weight': 1},
    54: {'source': 2, 'target': 1184, 'weight': 1},
    55: {'source': 2, 'target': 1185, 'weight': 1},
   

{   0: {'source': 1, 'target': 2, 'weight': 1},
    1: {'source': 2, 'target': 7, 'weight': 1},
    2: {'source': 2, 'target': 12, 'weight': 1},
    3: {'source': 2, 'target': 31, 'weight': 1},
    4: {'source': 58, 'target': 59, 'weight': 1},
    5: {'source': 2, 'target': 18, 'weight': 1},
    6: {'source': 18, 'target': 1, 'weight': 1},
    7: {'source': 2, 'target': 37, 'weight': 1},
    9: {'source': 37, 'target': 18, 'weight': 1},
    10: {'source': 2, 'target': 277, 'weight': 1},
    11: {'source': 1, 'target': 335, 'weight': 1},
    12: {'source': 18, 'target': 2, 'weight': 1},
    13: {'source': 2, 'target': 1, 'weight': 1},
    14: {'source': 471, 'target': 472, 'weight': 1},
    15: {'source': 58, 'target': 489, 'weight': 1},
    16: {'source': 58, 'target': 490, 'weight': 1},
    17: {'source': 489, 'target': 490, 'weight': 1},
    18: {'source': 9, 'target': 2, 'weight': 1},
    19: {'source': 1, 'target': 3, 'weight': 1},
    21: {'source': 750, 'target': 751, 'weight': 1

...

{   0: {'source': 1, 'target': 2, 'weight': 1},
    1: {'source': 2, 'target': 7, 'weight': 1},
    2: {'source': 2, 'target': 12, 'weight': 1},
    3: {'source': 2, 'target': 31, 'weight': 1},
    4: {'source': 58, 'target': 59, 'weight': 1},
    5: {'source': 2, 'target': 18, 'weight': 1},
    6: {'source': 18, 'target': 1, 'weight': 1},
    7: {'source': 2, 'target': 37, 'weight': 1},
    9: {'source': 37, 'target': 18, 'weight': 1},
    10: {'source': 2, 'target': 277, 'weight': 1},
    11: {'source': 1, 'target': 335, 'weight': 1},
    12: {'source': 18, 'target': 2, 'weight': 1},
    13: {'source': 2, 'target': 1, 'weight': 1},
    14: {'source': 471, 'target': 472, 'weight': 1},
    15: {'source': 58, 'target': 489, 'weight': 1},
    16: {'source': 58, 'target': 490, 'weight': 1},
    17: {'source': 489, 'target': 490, 'weight': 1},
    18: {'source': 9, 'target': 2, 'weight': 1},
    19: {'source': 1, 'target': 3, 'weight': 1},
    21: {'source': 750, 'target': 751, 'weight': 1

    375: {'source': 750, 'target': 13016, 'weight': 1},
    376: {'source': 750, 'target': 59, 'weight': 1},
    377: {'source': 13016, 'target': 59, 'weight': 1},
    380: {'source': 18, 'target': 1060, 'weight': 1},
    382: {'source': 669, 'target': 13125, 'weight': 1},
    383: {'source': 669, 'target': 8263, 'weight': 1},
    384: {'source': 669, 'target': 13127, 'weight': 1},
    385: {'source': 13125, 'target': 8263, 'weight': 1},
    386: {'source': 13125, 'target': 13127, 'weight': 1},
    387: {'source': 8263, 'target': 13127, 'weight': 1},
    388: {'source': 490, 'target': 669, 'weight': 1},
    389: {'source': 490, 'target': 13016, 'weight': 1},
    390: {'source': 490, 'target': 59, 'weight': 1},
    391: {'source': 669, 'target': 13016, 'weight': 1},
    394: {'source': 2, 'target': 13667, 'weight': 1},
    395: {'source': 1, 'target': 37, 'weight': 1},
    396: {'source': 2, 'target': 13976, 'weight': 1},
    397: {'source': 209, 'target': 1, 'weight': 1}}
breakpoint 2


    271: {'source': 2, 'target': 8578, 'weight': 1},
    272: {'source': 1, 'target': 511, 'weight': 1},
    273: {'source': 18, 'target': 3100, 'weight': 1},
    274: {'source': 86, 'target': 2, 'weight': 1},
    278: {'source': 140, 'target': 1, 'weight': 1},
    279: {'source': 140, 'target': 70, 'weight': 1},
    280: {'source': 140, 'target': 2, 'weight': 1},
    283: {'source': 70, 'target': 2, 'weight': 1},
    284: {'source': 9368, 'target': 9369, 'weight': 1},
    286: {'source': 1015, 'target': 1, 'weight': 1},
    287: {'source': 1015, 'target': 2953, 'weight': 1},
    291: {'source': 2, 'target': 1016, 'weight': 1},
    292: {'source': 12, 'target': 1589, 'weight': 1},
    293: {'source': 12, 'target': 1016, 'weight': 1},
    294: {'source': 1589, 'target': 1016, 'weight': 1},
    296: {'source': 37, 'target': 1, 'weight': 1},
    299: {'source': 58, 'target': 10176, 'weight': 1},
    300: {'source': 10224, 'target': 2, 'weight': 1},
    301: {'source': 1719, 'target': 4076

    158: {'source': 4339, 'target': 1325, 'weight': 1},
    159: {'source': 4339, 'target': 2459, 'weight': 1},
    160: {'source': 669, 'target': 4341, 'weight': 1},
    161: {'source': 669, 'target': 1325, 'weight': 1},
    162: {'source': 669, 'target': 2459, 'weight': 1},
    163: {'source': 4341, 'target': 1325, 'weight': 1},
    164: {'source': 4341, 'target': 2459, 'weight': 1},
    165: {'source': 1325, 'target': 2459, 'weight': 1},
    167: {'source': 9, 'target': 1, 'weight': 1},
    168: {'source': 9, 'target': 1057, 'weight': 1},
    169: {'source': 1, 'target': 1057, 'weight': 1},
    171: {'source': 58, 'target': 4860, 'weight': 1},
    174: {'source': 2, 'target': 209, 'weight': 1},
    176: {'source': 2, 'target': 4939, 'weight': 1},
    177: {'source': 2, 'target': 1736, 'weight': 1},
    180: {'source': 9, 'target': 18, 'weight': 1},
    181: {'source': 9, 'target': 4939, 'weight': 1},
    182: {'source': 9, 'target': 1736, 'weight': 1},
    183: {'source': 1, 'target

{   0: {'source': 1, 'target': 2, 'weight': 1},
    1: {'source': 2, 'target': 7, 'weight': 1},
    2: {'source': 2, 'target': 12, 'weight': 1},
    3: {'source': 2, 'target': 31, 'weight': 1},
    4: {'source': 58, 'target': 59, 'weight': 1},
    5: {'source': 2, 'target': 18, 'weight': 1},
    6: {'source': 18, 'target': 1, 'weight': 1},
    7: {'source': 2, 'target': 37, 'weight': 1},
    9: {'source': 37, 'target': 18, 'weight': 1},
    10: {'source': 2, 'target': 277, 'weight': 1},
    11: {'source': 1, 'target': 335, 'weight': 1},
    12: {'source': 18, 'target': 2, 'weight': 1},
    13: {'source': 2, 'target': 1, 'weight': 1},
    14: {'source': 471, 'target': 472, 'weight': 1},
    15: {'source': 58, 'target': 489, 'weight': 1},
    16: {'source': 58, 'target': 490, 'weight': 1},
    17: {'source': 489, 'target': 490, 'weight': 1},
    18: {'source': 9, 'target': 2, 'weight': 1},
    19: {'source': 1, 'target': 3, 'weight': 1},
    21: {'source': 750, 'target': 751, 'weight': 1

In [56]:
print(type(accent_edges))
pp.pprint(accent_edges)

<class 'dict'>
{   0: {'source': 1, 'target': 2, 'weight': 12},
    1: {'source': 2, 'target': 7, 'weight': 1},
    2: {'source': 2, 'target': 12, 'weight': 2},
    3: {'source': 2, 'target': 31, 'weight': 1},
    4: {'source': 58, 'target': 59, 'weight': 1},
    5: {'source': 2, 'target': 18, 'weight': 7},
    6: {'source': 18, 'target': 1, 'weight': 3},
    7: {'source': 2, 'target': 37, 'weight': 4},
    9: {'source': 37, 'target': 18, 'weight': 1},
    10: {'source': 2, 'target': 277, 'weight': 2},
    11: {'source': 1, 'target': 335, 'weight': 1},
    12: {'source': 18, 'target': 2, 'weight': 3},
    13: {'source': 2, 'target': 1, 'weight': 20},
    14: {'source': 471, 'target': 472, 'weight': 1},
    15: {'source': 58, 'target': 489, 'weight': 1},
    16: {'source': 58, 'target': 490, 'weight': 1},
    17: {'source': 489, 'target': 490, 'weight': 1},
    18: {'source': 9, 'target': 2, 'weight': 2},
    19: {'source': 1, 'target': 3, 'weight': 2},
    21: {'source': 750, 'target':

In [57]:
# check to see how many duplicates were removed - looks like about 50, or about a quarter
# so it's worth calculating a 'value' for each edge to signify its weight
print(len(accent_edges))

317


### Remove bidirectional edges

Now, we want to deduplicate the **edges** because graph we want to draw is not a _directed graph_. 

That is, the direction of links between nodes is not relevant for the analysis. 

To do this, we compare the `source` and the `target` of each of the edges, and if the `source` and `target` match the `target` and `source` of the edge being compared, we flag that edge for deletion. We then delete those edges flagged for deletion. 

In [58]:

deletion_list = [] # list to keep track of the dict keys that should be deleted 

for edge in accent_edges.items(): 
    #print (node) 
        
    for inner_edge in accent_edges.items(): 
        #pp.pprint(edge)
        #pp.pprint(inner_edge)
            
        # create values to compare on 
        edge_source_target = (edge[1]['source'], edge[1]['target'])
        edge_target_source = (edge[1]['target'], edge[1]['source'])
        inner_edge_target_source = (inner_edge[1]['target'], inner_edge[1]['source'])
        inner_edge_source_target = (inner_edge[1]['source'], inner_edge[1]['target'])
        
        

        if edge_source_target == inner_edge_target_source: # match, remove it 
                
            print ('match')
            print(edge_source_target)
            print(inner_edge_target_source)
                
            # we need to check that the outer edge is not already on the deletion_list 
            # otherwise we end up removing *all* the edges, not just the duplicates 
            
            # we need to also check that the transverse of the outer edge is not already on the deletion_list
            # otherwise we will end up deleting *both* of the edges
            # not just one of them 
            
            if (([inner_edge[0], edge[0]]) not in deletion_list) \
            and (([edge[0], inner_edge[0]]) not in deletion_list) : 
                deletion_list.append([inner_edge[0], edge[0]])
                print ('added ', ([inner_edge[0], edge[0]]), ' to deletion_list')
                

    

            
            

match
(1, 2)
(1, 2)
added  [13, 0]  to deletion_list
match
(1, 18)
(1, 18)
added  [6, 88]  to deletion_list
match
(1, 1015)
(1, 1015)
added  [286, 111]  to deletion_list
match
(1, 209)
(1, 209)
added  [397, 183]  to deletion_list
match
(1, 70)
(1, 70)
added  [34, 230]  to deletion_list
match
(1, 9)
(1, 9)
added  [167, 355]  to deletion_list
match
(1, 37)
(1, 37)
added  [296, 395]  to deletion_list
match
(2, 18)
(2, 18)
added  [12, 5]  to deletion_list
match
(2, 37)
(2, 37)
added  [209, 7]  to deletion_list
match
(2, 1)
(2, 1)
match
(2, 70)
(2, 70)
added  [283, 30]  to deletion_list
match
(2, 86)
(2, 86)
added  [274, 80]  to deletion_list
match
(2, 9)
(2, 9)
added  [18, 85]  to deletion_list
match
(2, 209)
(2, 209)
added  [28, 174]  to deletion_list
match
(2, 1736)
(2, 1736)
added  [83, 177]  to deletion_list
match
(2, 5068)
(2, 5068)
added  [338, 195]  to deletion_list
match
(2, 140)
(2, 140)
added  [280, 369]  to deletion_list
match
(9, 2)
(9, 2)
match
(9, 209)
(9, 209)
added  [359, 6

In [59]:
print (deletion_list)

[[13, 0], [6, 88], [286, 111], [397, 183], [34, 230], [167, 355], [296, 395], [12, 5], [209, 7], [283, 30], [274, 80], [18, 85], [28, 174], [83, 177], [338, 195], [280, 369], [359, 60], [84, 182], [9, 199]]


In [60]:
print (len(deletion_list))



19


In [61]:
# delete the edges in the deletion list, but transfer their weights to the edge that was de-duplicated

for edge_pair in deletion_list: 
    print(accent_edges[edge_pair[1]])
    print(accent_edges[edge_pair[0]])
    
    print('now deleting: ', edge_pair[0])
    
    print(accent_edges[edge_pair[1]]['weight'])
    print(accent_edges[edge_pair[0]]['weight'])
    
    
    print ('now adding weights to: ', edge_pair[1])
    accent_edges[edge_pair[1]]['weight'] += accent_edges[edge_pair[0]]['weight']
    print(accent_edges[edge_pair[1]]['weight'])
    del accent_edges[edge_pair[0]]
    

    

{'source': 1, 'target': 2, 'weight': 12}
{'source': 2, 'target': 1, 'weight': 20}
now deleting:  13
12
20
now adding weights to:  0
32
{'source': 1, 'target': 18, 'weight': 4}
{'source': 18, 'target': 1, 'weight': 3}
now deleting:  6
4
3
now adding weights to:  88
7
{'source': 1, 'target': 1015, 'weight': 1}
{'source': 1015, 'target': 1, 'weight': 1}
now deleting:  286
1
1
now adding weights to:  111
2
{'source': 1, 'target': 209, 'weight': 3}
{'source': 209, 'target': 1, 'weight': 1}
now deleting:  397
3
1
now adding weights to:  183
4
{'source': 1, 'target': 70, 'weight': 2}
{'source': 70, 'target': 1, 'weight': 1}
now deleting:  34
2
1
now adding weights to:  230
3
{'source': 1, 'target': 9, 'weight': 1}
{'source': 9, 'target': 1, 'weight': 3}
now deleting:  167
1
3
now adding weights to:  355
4
{'source': 1, 'target': 37, 'weight': 1}
{'source': 37, 'target': 1, 'weight': 1}
now deleting:  296
1
1
now adding weights to:  395
2
{'source': 2, 'target': 18, 'weight': 7}
{'source': 18,

In [62]:

print(len(accent_edges)) # this should equal the count before the de-duplication

298


In [63]:
pp.pprint(accent_edges)

{   0: {'source': 1, 'target': 2, 'weight': 32},
    1: {'source': 2, 'target': 7, 'weight': 1},
    2: {'source': 2, 'target': 12, 'weight': 2},
    3: {'source': 2, 'target': 31, 'weight': 1},
    4: {'source': 58, 'target': 59, 'weight': 1},
    5: {'source': 2, 'target': 18, 'weight': 10},
    7: {'source': 2, 'target': 37, 'weight': 6},
    10: {'source': 2, 'target': 277, 'weight': 2},
    11: {'source': 1, 'target': 335, 'weight': 1},
    14: {'source': 471, 'target': 472, 'weight': 1},
    15: {'source': 58, 'target': 489, 'weight': 1},
    16: {'source': 58, 'target': 490, 'weight': 1},
    17: {'source': 489, 'target': 490, 'weight': 1},
    19: {'source': 1, 'target': 3, 'weight': 2},
    21: {'source': 750, 'target': 751, 'weight': 1},
    22: {'source': 2, 'target': 763, 'weight': 1},
    24: {'source': 2, 'target': 776, 'weight': 1},
    25: {'source': 2, 'target': 777, 'weight': 1},
    26: {'source': 776, 'target': 777, 'weight': 1},
    27: {'source': 2, 'target': 782,

In [64]:
pp.pprint(accent_nodes)

{   0: [1, 2],
    1: [3],
    2: [1],
    3: [2],
    4: [2, 7],
    5: [1],
    6: [9],
    7: [2],
    8: [2, 12],
    9: [2],
    10: [2],
    11: [15],
    12: [2],
    13: [2],
    14: [18],
    15: [2],
    16: [2],
    17: [1],
    18: [18],
    19: [1],
    20: [2],
    21: [15],
    22: [9],
    23: [1],
    24: [18],
    25: [2],
    26: [2, 31],
    27: [18],
    28: [18],
    29: [2],
    30: [2],
    31: [18],
    32: [37],
    33: [2],
    34: [18],
    35: [18],
    36: [2],
    37: [18],
    38: [2],
    39: [3],
    40: [2],
    41: [1],
    42: [1],
    43: [2],
    44: [1],
    45: [2],
    46: [1],
    47: [15],
    48: [2],
    49: [1],
    50: [2],
    51: [1],
    52: [2],
    53: [58, 59],
    54: [2],
    55: [18],
    56: [18],
    57: [2],
    58: [18],
    59: [9],
    60: [18],
    61: [18],
    62: [2],
    63: [1],
    64: [70],
    65: [2],
    66: [18],
    67: [2],
    68: [18],
    69: [2],
    70: [2],
    71: [2],
    72: [1],
    73: [79],
    74:

    2212: [2],
    2213: [9],
    2214: [302],
    2215: [2],
    2216: [2],
    2217: [2],
    2218: [2],
    2219: [2],
    2220: [2],
    2221: [2],
    2222: [1],
    2223: [2],
    2224: [2],
    2225: [2],
    2226: [2],
    2227: [1],
    2228: [2],
    2229: [18],
    2230: [18],
    2231: [2],
    2232: [2],
    2233: [18],
    2234: [2],
    2235: [2],
    2236: [2],
    2237: [18],
    2238: [9],
    2239: [18],
    2240: [18],
    2241: [2],
    2242: [2],
    2243: [1587],
    2244: [9],
    2245: [18],
    2246: [302],
    2247: [1],
    2248: [2],
    2249: [1],
    2250: [2],
    2251: [3],
    2252: [2],
    2253: [2],
    2254: [37],
    2255: [18],
    2256: [15],
    2257: [86],
    2258: [18],
    2259: [2],
    2260: [18],
    2261: [2],
    2262: [2],
    2263: [2],
    2264: [18],
    2265: [18],
    2266: [2],
    2267: [1],
    2268: [2],
    2269: [2],
    2270: [511],
    2271: [18],
    2272: [37],
    2273: [2],
    2274: [86],
    2275: [2],
    2276: [1]

    3601: [1],
    3602: [9],
    3603: [15],
    3604: [37],
    3605: [18],
    3606: [18],
    3607: [2],
    3608: [2],
    3609: [2],
    3610: [1],
    3611: [2],
    3612: [15],
    3613: [18],
    3614: [2],
    3615: [37],
    3616: [2],
    3617: [37],
    3618: [2],
    3619: [2],
    3620: [2],
    3621: [209],
    3622: [1],
    3623: [2],
    3624: [1],
    3625: [1],
    3626: [2],
    3627: [2],
    3628: [2],
    3629: [2],
    3630: [18],
    3631: [2],
    3632: [2],
    3633: [2],
    3634: [18],
    3635: [18],
    3636: [37],
    3637: [2],
    3638: [2],
    3639: [2],
    3640: [2],
    3641: [18],
    3642: [2],
    3643: [1],
    3644: [9],
    3645: [1],
    3646: [1],
    3647: [2],
    3648: [9],
    3649: [2],
    3650: [2],
    3651: [1],
    3652: [18],
    3653: [18],
    3654: [2],
    3655: [2],
    3656: [2],
    3657: [15],
    3658: [2],
    3659: [18],
    3660: [1],
    3661: [2],
    3662: [18],
    3663: [18],
    3664: [2],
    3665: [1],
    

    5121: [18, 37],
    5122: [18],
    5123: [1, 2],
    5124: [669],
    5125: [1],
    5126: [302],
    5127: [3],
    5128: [2],
    5129: [2],
    5130: [2],
    5131: [37],
    5132: [2],
    5133: [18],
    5134: [37],
    5135: [511],
    5136: [2],
    5137: [18],
    5138: [2],
    5139: [3],
    5140: [9],
    5141: [18],
    5142: [2],
    5143: [302],
    5144: [1],
    5145: [258],
    5146: [2],
    5147: [18],
    5148: [9],
    5149: [2],
    5150: [1],
    5151: [2],
    5152: [134],
    5153: [18],
    5154: [1],
    5155: [1],
    5156: [2],
    5157: [2],
    5158: [1],
    5159: [1],
    5160: [1],
    5161: [2],
    5162: [18],
    5163: [2],
    5164: [18],
    5165: [18],
    5166: [9],
    5167: [9],
    5168: [2],
    5169: [1],
    5170: [18],
    5171: [37],
    5172: [2],
    5173: [18],
    5174: [2],
    5175: [1],
    5176: [2],
    5177: [2],
    5178: [258],
    5179: [15],
    5180: [1],
    5181: [18],
    5182: [1],
    5183: [3],
    5184: [1],
  

    7465: [2],
    7466: [302],
    7467: [2],
    7468: [18],
    7469: [2, 1325],
    7470: [2],
    7471: [2],
    7472: [1],
    7473: [1],
    7474: [1],
    7475: [1],
    7476: [2],
    7477: [2],
    7478: [18],
    7479: [18],
    7480: [2],
    7481: [2],
    7482: [302],
    7483: [2],
    7484: [37],
    7485: [15],
    7486: [2],
    7487: [2],
    7488: [302],
    7489: [1],
    7490: [9, 1],
    7491: [9],
    7492: [37],
    7493: [1],
    7494: [1],
    7495: [1],
    7496: [9],
    7497: [2],
    7498: [2],
    7499: [18],
    7500: [15],
    7501: [2],
    7502: [2],
    7503: [86],
    7504: [2],
    7505: [1],
    7506: [2],
    7507: [209],
    7508: [2, 1106],
    7509: [2],
    7510: [37],
    7511: [1],
    7512: [2],
    7513: [2],
    7514: [2],
    7515: [18],
    7516: [2],
    7517: [2],
    7518: [18],
    7519: [2],
    7520: [2],
    7521: [2],
    7522: [15],
    7523: [2],
    7524: [37],
    7525: [18],
    7526: [1],
    7527: [2],
    7528: [2],
  

    9947: [2],
    9948: [2],
    9949: [1],
    9950: [2],
    9951: [2],
    9952: [37],
    9953: [1],
    9954: [2],
    9955: [70],
    9956: [2],
    9957: [15],
    9958: [9],
    9959: [1],
    9960: [18],
    9961: [9],
    9962: [2],
    9963: [9],
    9964: [9],
    9965: [1],
    9966: [2],
    9967: [2],
    9968: [2],
    9969: [1],
    9970: [2],
    9971: [15],
    9972: [2],
    9973: [511],
    9974: [2],
    9975: [2],
    9976: [15],
    9977: [9],
    9978: [2],
    9979: [70],
    9980: [58, 10176],
    9981: [1],
    9982: [2],
    9983: [2],
    9984: [2],
    9985: [15],
    9986: [86],
    9987: [18],
    9988: [15],
    9989: [9],
    9990: [2],
    9991: [2],
    9992: [2],
    9993: [2],
    9994: [2],
    9995: [2],
    9996: [511],
    9997: [37],
    9998: [2],
    9999: [2],
    10000: [2],
    10001: [2],
    10002: [2],
    10003: [2],
    10004: [2],
    10005: [2],
    10006: [2],
    10007: [1],
    10008: [2],
    10009: [2],
    10010: [37],
    

    12084: [15],
    12085: [2],
    12086: [2],
    12087: [9],
    12088: [37],
    12089: [1],
    12090: [2],
    12091: [18],
    12092: [2],
    12093: [209],
    12094: [2],
    12095: [1],
    12096: [2],
    12097: [1],
    12098: [9],
    12099: [86],
    12100: [2],
    12101: [2],
    12102: [1],
    12103: [9],
    12104: [1],
    12105: [2],
    12106: [1],
    12107: [2],
    12108: [37],
    12109: [37],
    12110: [2],
    12111: [86],
    12112: [1],
    12113: [2],
    12114: [37],
    12115: [2],
    12116: [2],
    12117: [2],
    12118: [1],
    12119: [2],
    12120: [140],
    12121: [2],
    12122: [209],
    12123: [2],
    12124: [2],
    12125: [2],
    12126: [1],
    12127: [1],
    12128: [2],
    12129: [12349],
    12130: [2],
    12131: [1],
    12132: [209],
    12133: [86],
    12134: [2],
    12135: [1],
    12136: [18],
    12137: [18],
    12138: [2],
    12139: [1],
    12140: [18],
    12141: [1],
    12142: [2],
    12143: [2],
    12144: [2],


    14482: [2],
    14483: [2],
    14484: [1],
    14485: [1],
    14486: [2],
    14487: [2],
    14488: [2],
    14489: [2],
    14490: [2],
    14491: [2],
    14492: [37],
    14493: [2],
    14494: [2],
    14495: [2],
    14496: [302],
    14497: [37],
    14498: [2],
    14499: [2],
    14500: [9],
    14501: [37],
    14502: [15],
    14503: [2],
    14504: [1],
    14505: [2],
    14506: [2],
    14507: [2],
    14508: [209],
    14509: [2],
    14510: [2],
    14511: [2],
    14512: [9],
    14513: [2, 14776, 14777, 1325],
    14514: [18],
    14515: [1],
    14516: [1],
    14517: [1],
    14518: [1],
    14519: [70],
    14520: [18],
    14521: [2],
    14522: [2],
    14523: [2],
    14524: [2, 1186],
    14525: [2],
    14526: [9],
    14527: [2],
    14528: [70],
    14529: [2],
    14530: [37],
    14531: [1],
    14532: [2],
    14533: [18],
    14534: [18],
    14535: [70],
    14536: [2],
    14537: [18],
    14538: [1],
    14539: [1],
    14540: [2],
    14541: [9

In [65]:
# let's do some sanity checking to make sure these are correct 

# 0: {'source': 1, 'target': 2, 'weight': 32}
# this is equivalent to the occurrence [1, 2] in accent_nodes 
# plus the occurrences of [2, 1] because we have removed bidirectional edges
# plus any occurrences where 1 or 2 occur in a list, such as [1, 5, 17, 2]
# and represents a relationship between 
# 'England English' - accent id 1 - and 'United States English' - accent id 2

for idx, node in accent_nodes.items(): 
    if (1 in node and 2 in node) :
        print ('match')

print ('---')
print ('there are 32 lines, excellent')
print ('---')


# 5: {'source': 2, 'target': 18, 'weight': 10},

for idx, node in accent_nodes.items(): 
    if (18 in node and 2 in node) :
        print ('match')

print ('---')
print ('there are 10 lines, excellent')
print ('---')

# 64: {'source': 2, 'target': 1325, 'weight': 16}

for idx, node in accent_nodes.items(): 
    if (2 in node and 1325 in node) :
        print ('match')

print ('---')
print ('there are 16 lines, excellent')
print ('---')

match
match
match
match
match
match
match
match
match
match
match
match
match
match
match
match
match
match
match
match
match
match
match
match
match
match
match
match
match
match
match
match
---
there are 32 lines, excellent
---
match
match
match
match
match
match
match
match
match
match
---
there are 10 lines, excellent
---
match
match
match
match
match
match
match
match
match
match
match
match
match
match
match
match
---
there are 16 lines, excellent
---


In [66]:
# I am now confident that the edges are being represented correctly

In [67]:
# export the edges to a file 

filePath = 'accent_edges.json'

with open(filePath, "w") as outfile:
                json.dump(accent_edges, outfile)

## Some miscellaneous reporting for the paper

I want to get counts by the category of the accent descriptors and the predetermined accents. 

In [68]:
reload(cva)

predetermined = all_accents.reportPredeterminedAccents()
pp.pprint(predetermined)

[   ['United States English', 7537],
    ['England English', 2346],
    ['India and South Asia (India, Pakistan, Sri Lanka)', 2010],
    ['Canadian English', 897],
    ['Australian English', 665],
    ['Southern African (South Africa, Zimbabwe, Namibia)', 261],
    ['Irish English', 188],
    ['Scottish English', 172],
    ['New Zealand English', 163],
    ['Hong Kong English', 132],
    ['Filipino', 126],
    ['Malaysian English', 98],
    ['Singaporean English', 77],
    ['Welsh English', 67],
    ['West Indies and Bermuda (Bahamas, Bermuda, Jamaica, Trinidad)', 51],
    ['South Atlantic (Falkland Islands, Saint Helena)', 5]]


In [69]:
reload (cva) 
accent_category_counts = all_accents.reportAccentDescriptorCategories()
pp.pprint(accent_category_counts)

[   ['Subnational region', 45],
    ['Country', 42],
    ['Supranational region', 15],
    ['First or other language', 13],
    ['Register', 12],
    ['City', 10],
    ['Accent strength descriptor', 10],
    ['Vocal quality descriptor', 7],
    ['Mixed or variable accent', 5],
    ['Named Accent', 5],
    ['Specific phonetic changes', 3],
    ['Geographic region', 1],
    ['Accent effects due to physical changes', 1],
    ['Rhoticity', 1],
    ['Inflection', 1],
    ['Uncertainty marker', 1]]


In [70]:
reload (cva) 
accent_multi_descriptor_counts = all_accents.reportMultipleAccentDescriptors()
print(accent_multi_descriptor_counts)

more than two descriptors for:  pronounced
more than two descriptors for:  Received Pronunciation
more than two descriptors for:  classy
more than two descriptors for:  sassy
more than two descriptors for:  Kiwi
more than two descriptors for:  "Valley Girl" English
more than two descriptors for:  Conversational
[(472, <cvaccents.Accent object at 0x7f53ce8897c0>), (2715, <cvaccents.Accent object at 0x7f53d0648d30>), (3677, <cvaccents.Accent object at 0x7f53cbca2760>), (3678, <cvaccents.Accent object at 0x7f53cbca2790>), (5782, <cvaccents.Accent object at 0x7f53d06484f0>), (7056, <cvaccents.Accent object at 0x7f53d06485b0>), (12589, <cvaccents.Accent object at 0x7f53d0648cd0>)]


In [71]:
for accent in accent_multi_descriptor_counts: 
    print('\naccent is:', accent[1]._name)
    for descriptor in accent[1]._descriptors: 
        print(descriptor._name)


accent is: pronounced
Accent strength descriptor
Mixed or variable accent

accent is: Received Pronunciation
Register
Named Accent

accent is: classy
Vocal quality descriptor
Register

accent is: sassy
Vocal quality descriptor
Register

accent is: Kiwi
Country
Named Accent

accent is: "Valley Girl" English
Subnational region
Named Accent

accent is: Conversational
First or other language
Register
